## This script should compute the reaction fluxes and FVA intervals for the reactions of interest for Yarrowia lipolytica and Pichia pastoris
- Glycolysis
- Citrate cycle 
- Pentose Phosphate pathway
#### Metabolic maps only possible with BiKEGG in MATLAB
- Search for the reactions (id and name)
- Compare the found reactions between iYli21 and iMT1026v3 (based on name)
- Compare the found reactions with the reaction list

In [26]:
# imports
import cobra
from cobra.flux_analysis import flux_variability_analysis #fva

import yaml
import pandas as pd # load and modify csv data

from importlib import reload


# config preperation
import sys # append path

sys.path.append('../')
import helperFunction as hf
# reload(hf)

config_name = 'model_config'
config_path = f'../../config/{config_name}.yaml'

# load config
with open(config_path, 'r') as file:
    config = yaml.safe_load(file)

# global variables
_yli_maintenance = (7.8625, 7.8625)
_ppa_maintenance = (2.81, 2.81) # (according to the paper:https://www.ncbi.nlm.nih.gov/pmc/articles/PMC6838487/)


### Yarrowia lipolytica

#### Glycolysis

In [10]:
# loading the models
# load yli21 model
iYli21_model = cobra.io.read_sbml_model('../' + config['models']['yli21'])

# # load yli20 model
iYli20_model = cobra.io.read_sbml_model('../' +config['models']['yli2.0_corr'])

# # load iNL895 model
iNL895_model = cobra.io.read_sbml_model('../' +config['models']['yliNL895_corr'])

# # load yali4 model
iYali4_model = cobra.io.read_sbml_model('../' +config['models']['yli4_corr'])

# # load iMK735 model
iMK735_model = cobra.io.read_sbml_model('../' +config['models']['yliMK735_corr'])

# # load iYLI647 model (no EC numbers)
iYli647_model = cobra.io.read_sbml_model('../' +config['models']['yli647_corr'])

In [11]:
# Glycolysis dict with ec and reaction id for the models: iYli21, iYali4, iYli_2.0, iYLI647, iMK735
# Does other KEGG Maps have the same EC Numbers? Yes
# Set of EC Numbers:
glycolysis_without_branches = ["2.7.1.1", "5.3.1.9", "2.7.1.11", "4.1.2.13", "5.3.1.1", "1.2.1.12", "2.7.2.3", "5.4.2.11", "4.2.1.11", "2.7.1.40"]


iYli21_glycolysis_without_branches = {
    "2.7.1.1": "R387", # id="R387" name="hexokinase (D-glucose:ATP)"
    "5.3.1.9": "R326", # id="R326" name="glucose-6-phosphate isomerase"
    "2.7.1.11": "R636", # id="R636" name="phosphofructokinase"
    "ppp->ppp": "R714", # id="R714" name="ribulose 5-phosphate 3-epimerase" # D-ribulose 5-phosphate_C5H11O8P <=> D-xylulose 5-phosphate_C5H11O8P
    "4.1.2.13": "R313", # id="R313" name="fructose-bisphosphate aldolase"
    "4.1.2.13b": "R313", # id="R256" name="D-fructose 1-phosphate D-glyceraldehyde-3-phosphate-lyase"
    "5.3.1.1": "R768", # id="R768" name="triose-phosphate isomerase"
    "1.2.1.12": "R344", # id="R344" name="glyceraldehyde-3-phosphate dehydrogenase"
    "2.7.2.3": "R642", # id="R642" name="phosphoglycerate kinase"
    "5.4.2.11": "R643", # id="R643" name="phosphoglycerate mutase"
    "4.2.1.11": "R292", # id="R292" name="enolase", 
    "2.7.1.40": "R694",# id="R694" name="pyruvate kinase"
}

iYali4_glycolysis_without_branches = {
    "2.7.1.1": "534", # name="hexokinase (D-glucose:ATP)" id="R_534"
    "5.3.1.9": "467", # name="glucose-6-phosphate isomerase" id="R_467"
    "2.7.1.11": "886", # name="phosphofructokinase" id="R_886"
    "4.1.2.13": "450", # name="fructose-bisphosphate aldolase" id="R_450"
    "4.1.2.13b": "450", # id="R_322" name="D-fructose 1-phosphate D-glyceraldehyde-3-phosphate-lyase" alternative to the aldolase
    "5.3.1.1": "1054", # name="triose-phosphate isomerase" id="R_1054"
    "1.2.1.12": "486", # name="glyceraldehyde-3-phosphate dehydrogenase" id="R_486"
    "2.7.2.3": "892", # name="phosphoglycerate kinase" id="R_892"
    "5.4.2.11": "893", # name="phosphoglycerate mutase" id="R_893" 
    "4.2.1.11": "366", # name="enolase" id="R_366"
    "2.7.1.40": "962",# name="pyruvate kinase" id="R_962"
}

iYli647_glycolysis_without_branches = {
    "2.7.1.1": "HEX1", # id="R_HEX1" name="hexokinase D glucoseATP"
    "5.3.1.9": "PGI", # R_G6PI; R_PGI id="R_PGI" name="glucose 6 phosphate isomerase"
    "2.7.1.11": "PFK", # R_PFK_3; R_PFK_2; R_PFK id="R_PFK" name="phosphofructokinase"
    "4.1.2.13": "FBA", # R_FBA id="R_FBA" name="fructose bisphosphate aldolase"
    "5.3.1.1": "TPI", # R_TPI id="R_TPI" name="triose phosphate isomerase"
    "1.2.1.12": "GAPD", # R_GAPD id="R_GAPD" name="glyceraldehyde 3 phosphate dehydrogenase"
    "2.7.2.3": "PGK", # R_PGK id="R_PGK" name="phosphoglycerate kinase"
    "5.4.2.11": "PGM", # R_PGM id="R_PGM" name="phosphoglycerate mutase"
    "4.2.1.11": "ENO", # R_ENO id="R_ENO" name="enolase"
    "2.7.1.40": "PYK",# R_PYK id="R_PYK" name="pyruvate kinase"
}

iMK735_glycolysis_without_branches = {
    "2.7.1.1": "HEX1", # id="R_HEX1" name="R_hexokinase__D_glucoseATP_"
    "5.3.1.9": "PGI", # id="R_PGI" name="R_glucose_6_phosphate_isomerase"
    "2.7.1.11": "PFK", # id="R_PFK" name="R_phosphofructokinase"
    "4.1.2.13": "FBA", # id="R_FBA" name="R_fructose_bisphosphate_aldolase"
    "5.3.1.1": "TPI", # id="R_TPI" name="R_triose_phosphate_isomerase"
    "1.2.1.12": "GAPD", # id="R_GAPD" name="R_glyceraldehyde_3_phosphate_dehydrogenase"
    "2.7.2.3": "PGK", # id="R_PGK" name="R_phosphoglycerate_kinase"
    "5.4.2.11": "PGM", # id="R_PGM" name="R_phosphoglycerate_mutase" 
    "4.2.1.11": "ENO", # id="R_ENO" name="R_enolase"
    "2.7.1.40": "PYK",# id="R_PYK" name="R_pyruvate_kinase"
}

iNL865_glycolysis_without_branches = {
    "2.7.1.1": "r_0573", # id="r_0573" name="hexokinase (D-glucose:ATP)"
    "5.3.1.9": "r_0505", # id="r_0505" name="glucose-6-phosphate isomerase"
    "2.7.1.11": "r_0859", # id="r_0859" name="phosphofructokinase" sboTerm="SBO:0000176"
    "4.1.2.13": "r_0484", # id="r_0484" name="fructose-bisphosphate aldolase" sboTerm="SBO:0000176"
    "5.3.1.1": "r_1041", # id="r_1041" name="triose-phosphate isomerase" sboTerm="SBO:0000176"
    "1.2.1.12": "r_0525", # id="r_0525" name="glyceraldehyde-3-phosphate dehydrogenase" sboTerm="SBO:0000176"
    "2.7.2.3": "r_0865", # id="r_0865" name="phosphoglycerate kinase" sboTerm="SBO:0000176"
    "5.4.2.11": "r_0866", # id="r_0866" name="phosphoglycerate mutase" sboTerm="SBO:0000176"
    "4.2.1.11": "r_0398", # id="r_0398" name="enolase" sboTerm="SBO:0000176"
    "2.7.1.40": "r_0941",# id="r_0941" name="pyruvate kinase" sboTerm="SBO:0000176"
}

iYL_20_glycolysis_without_branches = {
    "2.7.1.1": "R0371", # id="R0371" name="ATP:beta-D-glucose 6-phosphotransferase"
    "5.3.1.9": "R0376", # id="R0376" name="alpha-D-Glucose 6-phosphate ketol-isomerase"
    "2.7.1.11": "R0379", # id="R0379" name="ATP:D-fructose-6-phosphate 1-phosphotransferase"
    "4.1.2.13": "R0368", # id="R0368" name="beta-D-fructose-1,6-bisphosphate D-glyceraldehyde-3-phosphate-lyase (glycerone-phosphate-forming)"
    "5.3.1.1": "R0366", # id="R0366" name="D-glyceraldehyde-3-phosphate aldose-ketose-isomerase"
    "1.2.1.12": "R0367", # id="R0367" name="D-glyceraldehyde-3-phosphate:NAD+ oxidoreductase (phosphorylating)"
    "2.7.2.3": "R0369", # id="R0369" name="ATP:3-phospho-D-glycerate 1-phosphotransferase"
    "5.4.2.11": "R0370", # id="R0370" name="2-Phospho-D-glycerate 2,3-phosphomutase"
    "4.2.1.11": "R0360", # id="R0360" name="2-phospho-D-glycerate hydro-lyase (phosphoenolpyruvate-forming)"
    "2.7.1.40": "R0382",# id="R0382" name="ATP:pyruvate 2-O-phosphotransferase"
}


###### Check if reation Ids are correct

In [4]:
# check reaction ids of iNL895
hf.metabolites_print(iNL895_model, 'r_0573')

# check reaction ids of iYali4_model (hexokinase)
hf.metabolites_print(iYali4_model, '534')

# check reaction ids of iMK735_model (hexokinase)
hf.metabolites_print(iMK735_model, 'HEX1')
 
# check reaction ids of iYli647_model (hexokinase)
hf.metabolites_print(iYli647_model, 'HEX1')

Metabolites for the reaction: hexokinase (D-glucose:ATP) (id: r_0573)
ATP[cy] (s_0446): -1.0
D-glucose[cy] (s_0545): -1.0
ADP[cy] (s_0400): 1.0
D-glucose 6-phosphate[cy] (s_0410): 1.0
Metabolites for the reaction: hexokinase (D-glucose:ATP) (id: 534)
ATP[cy] (m141): -1.0
D-glucose[cy] (m295): -1.0
H+_p+1[cy] (m10): 1.0
ADP[cy] (m143): 1.0
D-glucose 6-phosphate[cy] (m296): 1.0
Metabolites for the reaction: hexokinase D glucoseATP (id: HEX1)
ATP (atp[c]): -1.0
D_Glucose (glc_D[c]): -1.0
ADP (adp[c]): 1.0
D_Glucose_6_phosphate (g6p[c]): 1.0
H (h[c]): 1.0
Metabolites for the reaction: hexokinase D glucoseATP (id: HEX1)
D_Glucose (glc_D[c]): -1.0
ATP (atp[c]): -1.0
H (h[c]): 1.0
ADP (adp[c]): 1.0
D_Glucose_6_phosphate (g6p[c]): 1.0


True

##### Investigations regarding the correct reactions

In [14]:
## helpful functions
def compare_reactions(model, rxns):
    for rxn in rxns:
        if rxn in model.reactions:
            hf.reaction_print(model, rxn.id)
        else:
            print('Error: ', rxn, 'is not in model')

In [71]:
# # Yli21
# # not sure if R344 or R642 is the 6th step -> investigate the metabolites
# hf.metabolites_print(iYli21_model, 'R344') # -> glyceraldehyde 3-phosphate -> 1,3-bisphospho-D-glycerate
# hf.metabolites_print(iYli21_model, 'R642') # -> 1,3-bisphospho-D-glycerate -> 3-phosphoglycerate
# hf.metabolites_print(iYli21_model, 'R643') # -> 1,3-bisphospho-D-glycerate -> 3-phosphoglycerate

# # Yli_2.0
# # not sure which reaction is pyruvate kinase -> investigate the metabolites
# hf.metabolites_print(iYli20_model, 'R0382') # yes
# hf.metabolites_print(iYli20_model, 'R1554') # no
# hf.metabolites_print(iYli20_model, 'R1555') # no
# hf.metabolites_print(iYli20_model, 'R1558') # no


# looking for phosphoglycerate mutase
# hf.metabolites_print(iYli20_model, 'R0370') # different direction but yes
# hf.metabolites_print(iYli20_model, 'R1377') # no
# iYli20_model.reactions.get_by_id('R0370') => it is the phosphoglycerate mutase

# # looking for phosphoglycerate kinase
# hf.metabolites_print(iYli20_model, 'R0369') # 
# iYli20_model.reactions.get_by_id('R0369')

## looking for glyceraldehyde-3-phosphate dehydrogenase
# hf.metabolites_print(iYli20_model, 'R0367') # yes

## looking for triose-phosphate isomerase
# hf.metabolites_print(iYli20_model, 'R0366') # yes

## looking for fructose-bisphosphate aldolase
# hf.metabolites_print(iYli20_model, 'R0368') # yes

## looking for glucose-6-phosphate isomerase
# iYli20_model.reactions.get_by_id('R0376') # yes
# hf.metabolites_print(iYli20_model, 'R0376') # yes

## looking for hexokinase (D-glucose:ATP)
# glucosamine_rxn = iYli20_model.reactions.get_by_id('R0033') # => glucosamine Was ist das?
# hf.metabolites_print(iYli20_model, 'R0033') # => glucosamine Was ist das?
# iYli20_model.metabolites.get_by_id('M00322[c]') # => D-Glucosamine != D-Glucose
## compare hexokinase of yli21 with glucosamine_rxn
# hf.metabolites_print(iYli21_model, 'R387') # yes
# hexokinase_rxn = iYli21_model.reactions.get_by_id('R387')
# hexokinase_rxn
# glucosamine_rxn
## find glucose in iYli20_model
# for met in iYli20_model.metabolites:
#     if 'glucose' in met.name.lower():
#         print(met.id, met.name) 
# # => M00032[c] alpha-D-Glucose; M00605[c] alpha-D-Glucose 6-phosphate[c]

## investigate the reactions of alpha-D-Glucose and alpha-D-Glucose 6-phosphate
# D_glucose = iYli20_model.metabolites.get_by_id('M00032[c]')
# D_glucose_6_phosphate = iYli20_model.metabolites.get_by_id('M00605[c]')
# print("alpha-D-Glucose")
# for rxn in D_glucose.reactions:
#     hf.metabolites_print(iYli20_model, rxn.id)

# print("alpha-D-Glucose-6-phosphate")
# for rxn in D_glucose_6_phosphate.reactions:
#     hf.metabolites_print(iYli20_model, rxn.id)
# # => reaction: ATP:beta-D-glucose 6-phosphotransferase (id: R0371)

## compare R0371 with yli21 hexokinase
# hf.metabolites_print(iYli20_model, 'R0371') # -> hexokinase
# hf.metabolites_print(iYli21_model, 'R387')


### Investigate Yli model without EC numbers: iYli647_model
# hf.metabolites_print(iYli647_model, 'HEX1') # -> hexokinase

# check reactions I found multiple ids for:
## R_G6PI; R_PGI (glucose-6-phosphate isomerase)
# hf.metabolites_print(iYli647_model, 'G6PI') # D_Glucose_6_phosphate <=> beta_D_glucose_6_phosphate
# hf.metabolites_print(iYli647_model, 'PGI') # D_Glucose_6_phosphate <=> D_Fructose_6_phosphate (correct one)

## R_PFK_3; R_PFK_2; R_PFK (phosphofructokinase)
# hf.metabolites_print(iYli647_model, 'PFK_3') # no: Sedoheptulose_7_phosphate -> Sedoheptulose_1_7_bisphosphate
# hf.metabolites_print(iYli647_model, 'PFK_2') # no: D_Tagatose_6_phosphate + ATP <=> D_Tagatose_1_6_biphosphate + ADP
# hf.metabolites_print(iYli647_model, 'PFK') # yes: D_Fructose_6_phosphate + ATP <=> D_Fructose_1_6_bisphosphate + ADP


Metabolites for the reaction: phosphofructokinase s7p (id: PFK_3)
ATP (atp[c]): -1.0
Sedoheptulose_7_phosphate (s7p[c]): -1.0
H (h[c]): 1.0
ADP (adp[c]): 1.0
Sedoheptulose_1_7_bisphosphate (s17bp[c]): 1.0
Metabolites for the reaction: Phosphofructokinase (id: PFK_2)
ATP (atp[c]): -1.0
D_Tagatose_6_phosphate (tag6p_D[c]): -1.0
H (h[c]): 1.0
ADP (adp[c]): 1.0
D_Tagatose_1_6_biphosphate (tagdp_D[c]): 1.0
Metabolites for the reaction: phosphofructokinase (id: PFK)
ATP (atp[c]): -1.0
D_Fructose_6_phosphate (f6p[c]): -1.0
H (h[c]): 1.0
ADP (adp[c]): 1.0
D_Fructose_1_6_bisphosphate (fdp[c]): 1.0


True

#### Citrate Cycle:
- EC Numbers
- find reactions from iYli21 and iYali4 (iMT1026v3)


In [15]:
# iYli21
# group name: Citrate cycle (TCA cycle)
# for gr in iYli21_model.groups:
#     if 'cycle' in gr.name.lower():
#         print(gr.name, gr.id) # => Citrate cycle (TCA cycle) group14

for rxn in iYli21_model.groups.get_by_id('group14').members:
    formula = hf.formulaWithNames(rxn)
    print(rxn.notes, rxn.id, rxn.name, formula, rxn.reaction)
    

{'PROTEIN_CLASS': '2.3.3.8'} R1894 ATP-citrate lyase ATP_C10H16N5O13P3 + citrate_C6H8O7 + coenzyme A_C21H36N7O16P3S --> ADP_C10H15N5O10P2 + oxaloacetate_C4H4O5 + phosphate_H3O4P + acetyl-CoA_C23H38N7O17P3S m141[c] + m435[c] + m69[c] --> m143[c] + m328[c] + m35[c] + m68[c]
{'PROTEIN_CLASS': '1.3.5.1'} R740 succinate dehydrogenase (ubiquinone-6) ubiquinone-6_C39H58O4 + succinate_C4H6O4 <=> ubiquinol-6_C39H60O4 + fumarate_C4H4O4 m468[m] + m810[m] <=> m471[m] + m537[m]
{'PROTEIN_CLASS': '1.2.4.1'} R693 pyruvate dehydrogenase NAD_C21H27N7O14P2 + pyruvate_C3H4O3 + coenzyme A_C21H36N7O16P3S --> H+_p+1 + NADH_C21H29N7O14P2 + carbon dioxide_CO2 + acetyl-CoA_C23H38N7O17P3S m27[m] + m6[m] + m73[m] --> m28[m] + m30[m] + m44[m] + m71[m]
{'PROTEIN_CLASS': '1.1.1.42'} R1385 isocitrate dehydrogenase NADP(+)_C21H28N7O17P3 + isocitrate_C6H8O7 <=> NADPH_C21H30N7O17P3 + 2-oxoglutarate_C5H6O5 + carbon dioxide_CO2 m178[m] + m410[m] <=> m176[m] + m219[m] + m44[m]
{} R488 isocitrate dehydrogenase (NADP) NADP(

In [16]:
# check if citrate_C6H8O7 is in mitochondria
for met in iYli21_model.metabolites:
    if 'citrate_c6' in met.name.lower():
        print(met.id, met.name, met.compartment)

m410[m] isocitrate_C6H8O7 m
m433[m] citrate_C6H8O7 m
m434[C_pe] citrate_C6H8O7 C_pe
m435[c] citrate_C6H8O7 c
m738[c] isocitrate_C6H8O7 c
m739[C_pe] isocitrate_C6H8O7 C_pe
m1187[e] citrate_C6H8O7 e
m1803[e] isocitrate_C6H8O7 e


In [4]:
# load iMT1026v3 model
iMT1026v3_model = cobra.io.read_sbml_model(config['models']['ppa1026v3'])

In [ ]:
citrate_cycle_rxns = []
ec_numbers = []
for rxn in iMT1026v3_model.reactions:
    try:
        if 'citric acid cycle' in rxn.notes['SUBSYSTEM'].lower():
            citrate_cycle_rxns.append(rxn)
            try: 
                ec_numbers.append((rxn.id, rxn.name, rxn.reaction, rxn.notes['EC Number']))
            except:
                ec_numbers.append((rxn.id, 'no ec number given'))                
    except:
        pass
# print(len(citrate_cycle_rxns))
# print(citrate_cycle_rxns)
# hf.reactionInformationPrint(citrate_cycle_rxns)
ec_numbers

In [18]:
# check producing reaction of accoa_m
iMT1026v3_model.metabolites.get_by_id('accoa_m').summary() # => 100% PDHbrm

iMT1026v3_model.reactions.get_by_id('PDHbrm').notes # 2.3.1.12
iMT1026v3_model.reactions.get_by_id('PDHbrm').reaction # 'adhlam_m + coa_m + h_m --> accoa_m + dhlam_m'


'adhlam_m + coa_m + h_m --> accoa_m + dhlam_m'

In [12]:
# iMT1026v3
iMT1026v3_citrate_cycle = {
  '6.4.1.1': 'PC', # NOT MITOCHORIAL pyruvate carboxylase (Pyruvate -> Oxaloacetate)
  'pyruvate_mitochodrial_transport': 'PYRt2m', # pyruvate mitochondrial transport via proton symport
  '1.2.4.1': 'PDHa1', # pyruvate dehydrogenase (lipoamide)
  '1.2.4.1': 'PDHa2', # pyruvate dehydrogenase (lipoamide)
  '2.3.3.1': 'CSm', # citrate synthase (mitochondrial)
  '4.2.1.3': 'ACONTm', # aconitase (mitochondrial)
  '1.1.1.41': 'ICDHxm', # isocitrate dehydrogenase (NAD+)
  '1.2.4.2': 'AKGDH1', # 2-oxoglutarate dehydrogenase
  '1.2.4.2': 'AKGDH2', # 2-oxoglutarate dehydrogenase
  '2.3.1.61': 'AKGDbm', # oxoglutarate dehydrogenase (dihydrolipoamide S-succinyltransferase) (mitochondrial)
  '6.2.1.4': 'SUCOASm', # Succinate--CoA ligase (ADP-forming)
  '1.3.5.1': 'SUCD2_u6m', # succinate dehydrogenase (ubiquinone-6), mitochondrial
  '4.2.1.2': 'FUMm', # fumarase (mitochondrial)
  '1.1.1.37': 'MDHm', # malate dehydrogenase, mitochondrial
} 

# iYli21
iYli21_citrate_cycle = {
  '6.4.1.1': 'R690', # NOT MITOCHONRIAL pyruvate carboxylase (Pyruvate -> Oxaloacetate)
  'pyruvate_mitochodrial_transport': 'R1311', # pyruvate mitochondrial transport via proton symport
  '1.2.4.1': 'R693', # (m) pyruvate dehydrogenase (Pyruvate -> Acetyl-CoA)
  '2.3.3.1': 'R236', # (m) citrate synthase (Oxaloacetate + Acetyl-CoA -> Citrate)
  '4.2.1.3': 'R238', # (m) aconitase (citrate to cis-aconitate(3-)) # according to Expasy EC = 4.2.1.3
  '1.1.1.41': 'R487', # (m) isocitrate dehydrogenase (NAD+)
  '1.2.4.2': 'R614', # (m) oxoglutarate dehydrogenase (lipoamide)
  '2.3.1.61': 'R613', # (m) oxoglutarate dehydrogenase (dihydrolipoamide S-succinyltransferase)
  '6.2.1.4': 'R741', # (m) succinate-CoA ligase (ADP-forming)
  '1.3.5.1': 'R740', # (m) succinate dehydrogenase (ubiquinone-6)
  '4.2.1.2': 'R314', # (m) fumarase (fumarate to malate)
  '1.1.1.37': 'R533', # (m) malate dehydrogenase (malate to oxaloacetate)
}


### Pichia pastoris

#### Glycolysis
- load models
- find reactions
- check reaction ids

In [10]:
# load models

# load iMT1026v3 model
iMT1026v3_model = cobra.io.read_sbml_model(config['models']['ppa1026v3'])
# ### chan2017 model (standardized biomass reaction) of iMT1026 - 2016
# iMK1026_Chan_model = cobra.io.read_sbml_model(config['models']['ppa1026Chan'])

# # load iLC915 model
iLC915_model = cobra.io.read_sbml_model(config['models']['ppaiLC915'])


In [13]:
# find reactions
iMT1026v3_glycolysis_without_branches = {
    "2.7.1.1": "HEX1", # id="R_HEX1" name="hexokinase (D-glucose:ATP)"
    "5.1.3.3": "GLUK", # +2.7.1.1 a-D-glucose -> b-D-g6p id="R_GLUK" Alternative pathway from glucose to fructose-6-phosphate
    "5.1.3.9b": "G6PI3", # id="R_G6PI3" name="glucose-6-phosphate isomerase (b-D-glucose-6P <=> b-D-fructose-6P)"
    "5.3.1.9": "PGI", # id="R_PGI" name="glucose-6-phosphate isomerase"
    "2.7.1.11": "PFK", # id="R_PFK" name="phosphofructokinase"
    "4.1.2.13": "FBA", # id="R_FBA" name="fructose-bisphosphate aldolase"
    "4.1.2.13b": "FBA2", # id="R_FBA2" name="D-Fructose 1-phosphate D-glyceraldehyde-3-phosphate-lyase" (alternative zu FBA)
    "5.3.1.1": "TPI", # id="R_TPI" name="triose-phosphate isomerase"
    "1.2.1.12": "GAPD", # id="R_GAPD" name="glyceraldehyde-3-phosphate dehydrogenase"
    "2.7.2.3": "PGK", # id="R_PGK" name="phosphoglycerate kinase"
    "5.4.2.11": "PGM", # id="R_PGM" name="phosphoglycerate mutase" # iMT1026v3: EC: 5.4.2.1
    "4.2.1.11": "ENO", # id="R_ENO" name="enolase"
    "2.7.1.40": "PYK",# id="R_PYK" name="pyruvate kinase" 
}

iLC915_glycolysis_without_branches = {
    "2.7.1.1": "r552", # id="R_r552" name="ATP:alpha-D-glucose 6-phosphotransferase"
    "5.3.1.9": "r984", # id="R_r984" name="beta-D-Glucose 6-phosphate ketol-isomerase"
    "PPP->glycer3p": "r319", # id="R_r319" name="sedoheptulose-7-phosphate:D-glyceraldehyde-3-phosphate"
    "2.7.1.11": "r557", # id="R_r557" name="ATP:D-fructose-6-phosphate 1-phosphotransferase"
    "4.1.2.13": "r872", # id="R_r872" name="beta-D-fructose-1,6-bisphosphate D-glyceraldehyde-3-phosphate-lyase" 
    "5.3.1.1": "r978", # id="R_r978" name="D-glyceraldehyde-3-phosphate aldose-ketose-isomerase"
    "1.2.1.12": "r146", # id="R_r146" name="D-glyceraldehyde-3-phosphate:NAD+ oxidoreductase (phosphorylating)" 
    "2.7.2.3": "r596", # id="R_r596" name="ATP:3-phospho-D-glycerate 1-phosphotransferase"
    "5.4.2.11": "r988", # id="R_r988" name="2-Phospho-D-glycerate 2,3-phosphomutase" 
    "4.2.1.11": "r891", # id="R_r891" name="2-phospho-D-glycerate hydro-lyase (phosphoenolpyruvate-forming)" 
    "2.7.1.40": "r576",# id="R_r576" name="ATP:pyruvate 2-O-phosphotransferase"
}


In [5]:
# check the reaction ids
# HEX1: hexokinase (D-glucose:ATP)
iMT1026v3_model.reactions.get_by_id('HEX1')

print('iLC915')
# iLC915
# check: id="R_r984" name="beta-D-Glucose 6-phosphate

# # compare iYli21 hexokinase with iLC915: id: r552 => r552 is the correct reactions
# iLC915_model.reactions.get_by_id('r552') # => ATP_C10H16N5O13P3 + alpha-D-Glucose_C6H12O6 --> ADP_C10H15N5O10P2 + alpha-D-Glucose 6-phosphate_C6H13O9P
# iYli21_model.reactions.get_by_id('R387')  # ATP + D-glucose --> H+_p+1 + ADP + D-glucose 6-phosphate
# # compare iYli20 with iYli21 and iLC915: id: r552
# iYli20_model.reactions.get_by_id('R0371') # ATP[c] + alpha-D-Glucose[c] --> ADP[c] + H+[c] + alpha-D-Glucose 6-phosphate[c]

# # check beta-D-Glucose 6-phosphate ketol-isomerase id: R_r984
# # compare it with R_r736
# iLC915_model.reactions.get_by_id('r984') # => alpha-D-Glucose 6-phosphate_C6H13O9P --> beta-D-Fructose 6-phosphate_C6H13O9P

# iLC915_model.reactions.get_by_id('r736') #=> it is wrong (alpha-D Glucose-6P -> alpha-D Glucose)

# checking R_r146 for 1.2.1.12
# compare with R_r978
iLC915_model.reactions.get_by_id('r146') # => D-Glyceraldehyde 3-phosphate + NAD + Orthophosphate <=> 3-Phospho-D-glyceroyl phosphate + NADH + H+_H
iLC915_model.reactions.get_by_id('r978') # => D-Glyceraldehyde 3-phosphate_C3H7O6P <=> Glycerone phosphate_C3H7O6P




iLC915


<Reaction r978 at 0x29c920730>

### Download metabolic map from KEGG (Biopython 1.79 or higher) [Source](https://nbviewer.org/github/widdowquinn/notebooks/blob/master/Biopython_KGML_intro.ipynb)
Still not working
And BiKEGG has OS specific code

In [18]:
# import 
import Bio # 1.81

from Bio.KEGG.REST import *
from Bio.KEGG.KGML import KGML_parser

from Bio.Graphics.ColorSpiral import ColorSpiral # how to use it? I want a range of colors for the flux values


In [81]:
yli_glycolysis = KGML_parser.read(kegg_get("yli00010", "kgml"))


In [101]:
# playing with pathway instance
print(yli_glycolysis)
print(type(yli_glycolysis))

print(yli_glycolysis.orthologs[0].graphics[0].name)

# # check genes (enzymes?): no
# for gene in yli_glycolysis.genes:
#     print(type(gene))
#     print(gene)

# # check reactions (enzymes?): no
# for rxn in yli_glycolysis.reaction_entries:
#     print(type(rxn))

# check compounds (enzymes?): no
# for compound in yli_glycolysis.compounds:
#     print(compound.id)

Pathway: Glycolysis / Gluconeogenesis
KEGG ID: path:yli00010
Image file: https://www.kegg.jp/kegg/pathway/yli/yli00010.png
Organism: yli
Entries: 102
Entry types:
	ortholog: 37
	gene: 27
	compound: 31
	map: 7

<class 'Bio.KEGG.KGML.KGML_pathway.Pathway'>
K01905...


In [105]:
# plot test (coloring based on flux values)
from Bio.Graphics.KGML_vis import KGMLCanvas
from Bio.Graphics.ColorSpiral import ColorSpiral

# Helper function to convert colour as RGB tuple to hex string
def rgb_to_hex(rgb):
    rgb = tuple([int(255*val) for val in rgb])
    return '#' + ''.join([hex(val)[2:] for val in rgb]).upper()


pathway = yli_glycolysis
# Define arbitrary colours
colorspiral = ColorSpiral()
colorlist = colorspiral.get_colors(len(pathway.orthologs))

# Change the colours of ortholog elements
for color, element in zip(colorlist, pathway.orthologs):
    for graphic in element.graphics:
        graphic.bgcolor = rgb_to_hex(color)

MissingPythonDependencyError: Please install ReportLab if you want to use Bio.Graphics. You can find ReportLab at http://www.reportlab.com/software/opensource/

In [ ]:
canvas = KGMLCanvas(pathway, import_imagemap=True)
canvas.draw("fab_map_new_colours.pdf")
PDF("fab_map_new_colours.pdf")

### From FBA solution to Reaction specific flux values

#### Get the flux values of the top 3 Yli models: 

In [14]:
### function for getting the reaction fluxes of interest (glycolysis)

def set_growth_condition(model, biomass_rxn, growth_condition, maintenance_rxn, maintenance):
    """Sets the growth condition of a given model
    @params: model (cobra model), biomass_rxn (str), growth_condition (dict), maintenance_rxn (str), maintenance (tuple of floats)"""
    # set objective function
    model.objective = biomass_rxn
    # set growth condition
    for rxn_id, flux in growth_condition.items():
        model.reactions.get_by_id(rxn_id).bounds = (-flux, flux)
    if maintenance_rxn != 'r1188':
        # set maintenance
        model.reactions.get_by_id(maintenance_rxn).bounds = maintenance

def get_reaction_fluxes(model, reactions, biomass_rxn, growth_condition, maintenance_rxn, maintenance, verbose=False):
    """Computes FBA solution of a given growth condition and returns the fluxes of the reactions of interest"""
    current_fluxes = {}

    # set growth condition
    set_growth_condition(model, biomass_rxn, growth_condition, maintenance_rxn, maintenance)
    # compute FBA solution
    # pfba solution
    pfba_solution = cobra.flux_analysis.pfba(model)
    if verbose:
        print(f'The objective value of the {model} is: {pfba_solution.fluxes[biomass_rxn]}')
    # collect pathway fluxes
    for ec_number, rxn_id in reactions.items():
        if rxn_id == "-":
            continue
        current_fluxes[ec_number] = (pfba_solution.fluxes[rxn_id],rxn_id)
    return current_fluxes

def get_fva_intervals(model, reactions, biomass_rxn, growth_condition, maintenance_rxn, maintenance, loopless=False, fva_solution="",verbose=False):
    """Computes FBA solution of a given growth condition and returns the fluxes of the reactions of interest"""
    current_fva_interval = {}
    
    # set growth condition
    set_growth_condition(model, biomass_rxn, growth_condition, maintenance_rxn, maintenance)
    
    # compute FVA solution if fva_solution == {}
    fva_solution = fva_solution if isinstance(fva_solution, pd.DataFrame) else cobra.flux_analysis.flux_variability_analysis(model, loopless=loopless)
    if verbose:
        print(f'The objective value of the {model} is: {fva_solution.loc[biomass_rxn]}')
    
    # collect pathway intervals
    for ec_number, rxn_id in reactions.items():
        if rxn_id == "-":
            continue
        current_fva_interval[ec_number] = (fva_solution.loc[rxn_id].minimum, fva_solution.loc[rxn_id].maximum)
    return fva_solution, current_fva_interval

In [10]:
# find fructose and glycerol reactions for the models
for model in [iYli647_model, iYali4_model, iYli21_model]:
    print(model)
    for rxn in model.exchanges:
        if 'glyce' in rxn.name.lower():
            print(rxn.id, rxn.name)

Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.


COBRAModel
EX_glyc(e) Glycerol exchange
iYali4_corr
1553 1-(sn-glycero-3-phospho)-1D-myo-inositol exchange
1554 1-acylglycerophosphocholine exchange
1808 glycerol exchange
2046 sn-glycero-3-phosphocholine exchange
M_iYli21
R950 1-(sn-glycero-3-phospho)-1D-myo-inositol exchange
R951 1-acylglycerophosphocholine exchange
R1141 glycerol exchange
R1322 sn-glycero-3-phosphocholine exchange


#### Yarrowia lipolytica (Glycolysis flux on glucose)

In [20]:
## Top 3 Yli models: iYli21_glycolysis_without_branches, iYali4_glycolysis_without_branches, iYli647_glycolysis_without_branches
# model specific parameters iYli21
print("iYli21: \n")
biomass_rxn = 'biomass_C'
maintenance_rxn = 'xMAINTENANCE'
growth_condition = {
    'R1070': 100, # glucose
    'R1065': 0, # fructose
    'R1141': 0, # glycerol
}
    
yli21_fluxes = get_reaction_fluxes(iYli21_model, iYli21_glycolysis_without_branches, biomass_rxn, growth_condition, maintenance_rxn, _yli_maintenance)
print(yli21_fluxes)

# iYali4 results
print("iYALI4: \n")
biomass_rxn = 'biomass_C'
maintenance_rxn = 'xMAINTENANCE'
growth_condition = {
    '1714': 100, # glucose
    '1709': 0, # fructose
    '1808': 0, # glycerol
}

yali4_fluxes = get_reaction_fluxes(iYali4_model, iYali4_glycolysis_without_branches, biomass_rxn, growth_condition, maintenance_rxn, _yli_maintenance)
print(yali4_fluxes)

# iYli647 results
print("iYLI647: \n")
biomass_rxn = 'biomass_C'
maintenance_rxn = 'ATPM'
growth_condition = {
    'EX_glc(e)': 100, # glucose
    'EX_fru(e)': 0, # fructose
    'EX_glyc(e)': 0, # glycerol
}

YLI4647_fluxes = get_reaction_fluxes(iYli647_model, iYli647_glycolysis_without_branches, biomass_rxn, growth_condition, maintenance_rxn, _yli_maintenance)
print(YLI4647_fluxes)

iYli21: 

{'2.7.1.1': (100.0, 'R387'), '5.3.1.9': (47.142993308763295, 'R326'), '2.7.1.11': (42.59649398301414, 'R636'), '4.1.2.13': (42.59649398301414, 'R313'), '5.3.1.1': (54.9087438514326, 'R768'), '1.2.1.12': (120.53662664661454, 'R344'), '2.7.2.3': (120.53662664661454, 'R642'), '5.4.2.11': (111.09945035057774, 'R643'), '4.2.1.11': (111.09945035057774, 'R292'), '2.7.1.40': (107.63755614616058, 'R694')}
iYALI4: 

{'2.7.1.1': (100.0, '534'), '5.3.1.9': (86.86451610305674, '467'), '2.7.1.11': (68.21706886044475, '886'), '4.1.2.13': (68.21706886044475, '450'), '5.3.1.1': (68.2035517691628, '1054'), '1.2.1.12': (133.83834387188065, '486'), '2.7.2.3': (133.83834387188065, '892'), '5.4.2.11': (124.41076965040317, '893'), '4.2.1.11': (124.41076965040317, '366'), '2.7.1.40': (120.95239783077824, '962')}
iYLI647: 

{'2.7.1.1': (100.0, 'HEX1'), '5.3.1.9': (36.42246449933276, 'PGI'), '2.7.1.11': (39.2793944578707, 'PFK'), '4.1.2.13': (39.2793944578707, 'FBA'), '5.3.1.1': (54.97616772133508, 'T

#### Pichia pastoris (Glycolysis on glucose)


In [39]:
# check contextualized model
(model, errors) = cobra.io.validate_sbml_model(config['models']['ppa1026v3_context'])
# SBML error: () in chemical formula; variable names contain whitespace
errors

{'SBML_FATAL': [],
 'SBML_ERROR': ["E0 (Error): SBML component consistency (fbc, L148); Chemical formula must be string; The value of attribute 'fbc:chemicalFormula' on the SBML <species> object must be set to a string consisting only of atomic names or user defined compounds and their occurrence.\nReference: L3V1 Fbc V3 Section 3.4\n Encountered '(' when expecting a capital letter. The chemicalFormula 'C2H4NO2R(C2H2NOR)n' has incorrect syntax.\n",
  "E1 (Error): SBML component consistency (fbc, L149); Chemical formula must be string; The value of attribute 'fbc:chemicalFormula' on the SBML <species> object must be set to a string consisting only of atomic names or user defined compounds and their occurrence.\nReference: L3V1 Fbc V3 Section 3.4\n Encountered '(' when expecting a capital letter. The chemicalFormula 'C4H6NO3R(C2H2NOR)n' has incorrect syntax.\n",
  "E2 (Error): SBML component consistency (fbc, L309); Chemical formula must be string; The value of attribute 'fbc:chemicalFor

In [16]:
# # load iMT1026v3 model
iMT1026v3_model = cobra.io.read_sbml_model('../' +config['models']['ppa1026v3'])

# load iMT1026v3 contextualized
# iMT1026v3_context_model = cobra.io.read_sbml_model(config['models']['ppa1026v3_context']) 

# # load iLC915 model
iLC915_model = cobra.io.read_sbml_model('../' +config['models']['ppaiLC915'])

_verbose = False

In [17]:
# prepare iLC915_model
# prepares iLC915_model if _verbose = True: it presents the coefficients of the most important reactions
print('iLC915 model: ')

# prepare iLC915_model: needed because of internal cycles and active reactions
# lower and upper bounds of several reactions should be set to zero according to supplementary material of iMT1026
constraints_2_zero = ['r66','r910','r1104','r239','r111','r106','r490','r791','r243','r252','r253','r307','r308','r404','r405','r1320','r639','r640','r641','r642','r649','r650','r651','r652','r645','r646','r643','r644','r653','r654','r655','r656','r534'] 
for rxn_id in constraints_2_zero:
    rxn = iLC915_model.reactions.get_by_id(rxn_id)
    rxn.bounds = (0,0)
# constraint formulate uptake because of not meaningful results
formulate_uptake = iLC915_model.reactions.get_by_id('r1143')
formulate_uptake.bounds = (0,0)
# important carbon sources (biotin, CO2, urea)
important_carbon = ['r1132','r1137','r1177']

# all carbon containing exchange reactions
carbon_exchange_rxns = ['r1122', 'r1123', 'r1124', 'r1126', 'r1127', 'r1129', 'r1130', 'r1131', 'r1132', 'r1134', 'r1135', 'r1137', 'r1138', 'r1139', 'r1140', 'r1141', 'r1144', 'r1145', 'r1146', 'r1147', 'r1148', 'r1149', 'r1151', 'r1152', 'r1153', 'r1154', 'r1155', 'r1156', 'r1157', 'r1158', 'r1161', 'r1162', 'r1163', 'r1165', 'r1167', 'r1168', 'r1170', 'r1172', 'r1173', 'r1174', 'r1175', 'r1176', 'r1177', 'r1178']

# set all carbon exchange reactions to 0 except important ones
for rxn_id in carbon_exchange_rxns:
    if rxn_id not in important_carbon:
        rxn = iLC915_model.reactions.get_by_id(rxn_id)
        rxn.bounds = (0,0)

# check definition of important rxns 
important_rxns = ['r1133', 'r1141', 'r1145', 'r1144', 'r1148', 'r1160', 'r1137', 'r1188']

if _verbose: 
    for rxn_id in important_rxns:
        rxn = iLC915_model.reactions.get_by_id(rxn_id)
        print(rxn.reactants, rxn.products, rxn.bounds)
        print(rxn_id, rxn.name, hf.formulaWithNames(rxn), 'rxn coefficient: ', rxn.get_coefficient(list(rxn.metabolites.keys())[0]))

# set objective and maintenance
biomass_rxn = 'r1339' # biomass
# set objective: 
iLC915_model.objective = 'r1339'

# set maintenance reaction
maintenance = 'r1188'
maintenance_rxn = iLC915_model.reactions.get_by_id(maintenance)
# maintenance_rxn.bounds = (_ppa_maintenance,_ppa_maintenance)
# maintenance_rxn.bounds = (1,1) # according to iLC915_model
maintenance_rxn.bounds = (1.2434,1.2434) # according to iLC915_model (1.2434 * 2.26 = 2.81)

try: 
    iLC915_model.summary()
except:
    print('iLC915 model: works as expected')

gluc = iLC915_model.reactions.get_by_id('r1145')
gluc.bounds = (-10,10)
try: 
    iLC915_model.summary()
    print('iLC915 model: works as expected')
except:
    print('iLC915 model: does not work as expected')

iLC915 model: 
iLC915 model: works as expected
iLC915 model: works as expected


In [90]:
gluc = iLC915_model.reactions.get_by_id('r1145')
iLC915_model.summary()

In [91]:
# test setting growth condition
growth_condition = {
    'r1145': 100, # glucose
    'r1144': 0, # fructose
    'r1148': 0, # glycerol
    'r1160': 1000, # O2
}
for rxn_id, flux in growth_condition.items():
    print(iLC915_model.reactions.get_by_id(rxn_id))
    print(-flux, flux)
    iLC915_model.reactions.get_by_id(rxn_id).bounds = (-flux, flux)
try: 
    cobra.flux_analysis.pfba(iLC915_model)
    print('iLC915 model: works as expected')
except:
    print('iLC915 model: does not work as expected')

iLC915_model.summary()

r1145:  <=> m2
-100 100
r1144:  --> m1334
0 0
r1148:  --> m1238
0 0
r1160:  --> m1232
-1000 1000
iLC915 model: works as expected


In [92]:
# list of models
# iMT1026v3_model, iLC915_model
# iMT1026v3_glycolysis_without_branches, iLC915_glycolysis_without_branches

# # find glucose, fructose and glycerol reactions for the models
# for model in [iMT1026v3_model, iLC915_model]:
#     print(model)
#     # find glucose, fructose and glycerol reactions
#     for rxn in model.exchanges:
#         if 'glyce' in rxn.name.lower():
#             print('Glycerol:\t')
#             print(rxn.id, rxn.name)
#         elif 'fruc' in rxn.name.lower():
#             print('Fructose:\t')
#             print(rxn.id, rxn.name)
#         elif 'gluc' in rxn.name.lower():
#             print('Glucose:\t')
#             print(rxn.id, rxn.name)
#     print("------ Biomass & Maintenance: -------")
#     # find maintenance and biomass reaction
#     for rxn in model.reactions:
#         if 'growth' in rxn.name.lower() or 'biomass' in rxn.name.lower():
#             print('Biomass: ')
#             print(rxn.id, rxn.name, rxn.reaction, rxn.bounds)
#         if 'maint' in rxn.name.lower() or 'gam' in rxn.name.lower():
#             print('Maintenance: ')
#             print(rxn.id, rxn.name, rxn.reaction, rxn.bounds)


# # iMT1026v3 results
model_name = 'iMT1026v3'
print(f"{model_name}: \n")
biomass_rxn = 'growth' # BIOMASS_glyc # (id:BIOMASS) Biomass composition # growth biomass_c --> biomass_e
maintenance_rxn = 'ATPM' # 0.55 
growth_condition = {
    'Ex_glc_D': 100, # glucose
    'Ex_fru': 0, # fructose
    'Ex_glyc': 0, # glycerol
    'Ex_o2': 1000, # O2
}
    
current_fluxes = get_reaction_fluxes(iMT1026v3_model, iMT1026v3_glycolysis_without_branches, biomass_rxn, growth_condition, maintenance_rxn, _ppa_maintenance)
print(current_fluxes)

model_name = 'iLC915'
print(f"{model_name}: \n")
biomass_rxn = 'r1339' # r1339 Growth # r1187 biomass formation
maintenance_rxn = 'r1188' # Maintenance
growth_condition = {
    'r1145': 100, # glucose
    'r1144': 0, # fructose
    'r1148': 0, # glycerol
    'r1160': 1000, # O2
}
# hf.prepare_iLC915_model(iLC915_model)
# different maintenance because of different definition
current_fluxes = get_reaction_fluxes(iLC915_model, iLC915_glycolysis_without_branches, biomass_rxn, growth_condition, maintenance_rxn, (1.2434,1.2434))
print(current_fluxes)

iMT1026v3: 

{'2.7.1.1': (60.723759864488386, 'HEX1'), '5.3.1.9': (0.0, 'PGI'), '2.7.1.11': (43.945778554868376, 'PFK'), '4.1.2.13': (43.945778554868376, 'FBA'), '5.3.1.1': (56.59616687938003, 'TPI'), '1.2.1.12': (123.81374257642445, 'GAPD'), '2.7.2.3': (-123.81374257642445, 'PGK'), '5.4.2.11': (-115.31283857980253, 'PGM'), '4.2.1.11': (115.31283857980253, 'ENO'), '2.7.1.40': (109.50650621282493, 'PYK')}
iLC915: 

{'2.7.1.1': (100.0, 'r552'), '5.3.1.9': (81.08541856513504, 'r984'), '2.7.1.11': (71.12308923079226, 'r557'), '4.1.2.13': (71.12308923079226, 'r872'), '5.3.1.1': (-73.3323395330741, 'r978'), '1.2.1.12': (149.3312141914173, 'r146'), '2.7.2.3': (-149.3312141914173, 'r596'), '5.4.2.11': (-129.88686353172685, 'r988'), '4.2.1.11': (129.88686353172685, 'r891'), '2.7.1.40': (125.3686567619376, 'r576')}


In [31]:
# check iLC915 model (negative fluxes: e.g. r978)
iLC915_model.reactions.get_by_id('r978') # => D-Glyceraldehyde 3-phosphate_C3H7O6P <=> Glycerone phosphate_C3H7O6P
# => fine, but weird, that the flux is that low

# check iLC915 model (very low hex1: r552)
iLC915_model.reactions.get_by_id('r552') # => richtiges Enzym aber sehr niedriger flux => größere investigation notwendig
# => finde ich ein sinvolleres Modell?


<Reaction r552 at 0x29e1ca100>

#### Citrate cycle Flux values

In [18]:
# iMT1026v3
iMT1026v3_citrate_cycle = {
  '6.4.1.1': 'PC', # NOT MITOCHORIAL pyruvate carboxylase (Pyruvate -> Oxaloacetate)
  '1.1.1.37': 'MDHm', # malate dehydrogenase, mitochondrial (Malate -> Oxaloacetate)
  'pyruvate_mitochodrial_transport': 'PYRt2m', # pyruvate mitochondrial transport via proton symport
  '1.2.4.1': 'PDHa1', # pyruvate dehydrogenase (lipoamide)
  '1.2.4.1_2': 'PDHa2', # pyruvate dehydrogenase (lipoamide)
  '2.3.1.12': 'PDHbrm', # pyruvate dehydrogenase (dihydrolipoamide) reversible (mitochondrial) 
  '2.3.3.1': 'CSm', # citrate synthase (mitochondrial)
  '4.2.1.3': 'ACONTm', # aconitase (mitochondrial)
  '1.1.1.41': 'ICDHxm', # isocitrate dehydrogenase (NAD+)
  '1.2.4.2_1': 'AKGDH1', # 2-oxoglutarate dehydrogenase
  '1.2.4.2_2': 'AKGDH2', # 2-oxoglutarate dehydrogenase
  '2.3.1.61': 'AKGDbm', # oxoglutarate dehydrogenase (dihydrolipoamide S-succinyltransferase) (mitochondrial)
  '6.2.1.4': 'SUCOASm', # Succinate--CoA ligase (ADP-forming) # according to KEGG: 6.2.1.4: GDP-forming
  '6.2.1.5': 'ITCOALm', # Itaconate--CoA ligase (ADP-forming), mitochondrial id="R_ITCOALm" (?)
  '1.3.5.1': 'SUCD2_u6m', # succinate dehydrogenase (ubiquinone-6), mitochondrial
  '4.2.1.2': 'FUMm', # fumarase (mitochondrial)
}

# # # iLC915 (unfinished)
# iLC915_citrate_cycle = {
#   '6.4.1.1': 'PC', # NOT MITOCHORIAL pyruvate carboxylase (Pyruvate -> Oxaloacetate)
#   '1.1.1.37': 'MDHm', # malate dehydrogenase, mitochondrial (Malate -> Oxaloacetate)
#   'pyruvate_mitochodrial_transport': 'PYRt2m', # pyruvate mitochondrial transport via proton symport
#   '1.2.4.1': 'PDHa1', # pyruvate dehydrogenase (lipoamide)
#   '1.2.4.1_2': 'PDHa2', # pyruvate dehydrogenase (lipoamide)
#   '2.3.1.12': 'PDHbrm', # pyruvate dehydrogenase (dihydrolipoamide) reversible (mitochondrial) 
#   '2.3.3.1': 'CSm', # citrate synthase (mitochondrial)
#   '4.2.1.3': 'ACONTm', # aconitase (mitochondrial)
#   '1.1.1.41': 'ICDHxm', # isocitrate dehydrogenase (NAD+)
#   '1.2.4.2_1': 'AKGDH1', # 2-oxoglutarate dehydrogenase
#   '1.2.4.2_2': 'AKGDH2', # 2-oxoglutarate dehydrogenase
#   '2.3.1.61': 'AKGDbm', # oxoglutarate dehydrogenase (dihydrolipoamide S-succinyltransferase) (mitochondrial)
#   '6.2.1.4': 'SUCOASm', # Succinate--CoA ligase (ADP-forming) # according to KEGG: 6.2.1.4: GDP-forming
#   '6.2.1.5': 'ITCOALm', # Itaconate--CoA ligase (ADP-forming), mitochondrial id="R_ITCOALm" (?)
#   '1.3.5.1': 'SUCD2_u6m', # succinate dehydrogenase (ubiquinone-6), mitochondrial
#   '4.2.1.2': 'FUMm', # fumarase (mitochondrial)
# }


# iYli21
iYli21_citrate_cycle = {
  '6.4.1.1': 'R690', # NOT MITOCHONRIAL pyruvate carboxylase (Pyruvate -> Oxaloacetate)
  'pyruvate_mitochodrial_transport': 'R1311', # pyruvate mitochondrial transport via proton symport
  '1.1.1.37': 'R533', # (m) malate dehydrogenase (NAD+) (Malate -> Oxaloacetate)
  '1.2.4.1': 'R693', # (m) pyruvate dehydrogenase (Pyruvate -> Acetyl-CoA)
  '2.3.3.1': 'R236', # (m) citrate synthase (Oxaloacetate + Acetyl-CoA -> Citrate)
  '4.2.1.3': 'R238', # (m) aconitase (citrate to cis-aconitate(3-)) # according to Expasy EC = 4.2.1.3
  '1.1.1.41': 'R487', # (m) isocitrate dehydrogenase (NAD+)
  '1.1.1.42': 'R1385', # (m) isocitrate dehydrogenase (NAD+)
  '1.2.4.2': 'R614', # (m) oxoglutarate dehydrogenase (lipoamide)
  '2.3.1.61': 'R613', # (m) oxoglutarate dehydrogenase (dihydrolipoamide S-succinyltransferase)
  '6.2.1.4': 'R741', # (m) succinate-CoA ligase (ADP-forming)
  '6.2.1.5': 'R496', # (m) itaconate-CoA ligase (ADP-forming) id="R496" (?)
  '1.3.5.1': 'R740', # (m) succinate dehydrogenase (ubiquinone-6)
  '4.2.1.2': 'R314', # (m) fumarase (fumarate to malate)
  '1.1.1.37': 'R533', # (m) malate dehydrogenase (malate to oxaloacetate)
}

# iYali4
iYali4_citrate_cycle = {
  '6.4.1.1': '958', # pyruvate carboxylase (id:R_958) (Pyruvate -> Oxaloacetate)
  '1.1.1.37': '713', # malate dehydrogenase (id:R_713) (Malate -> Oxaloacetate)
  'pyruvate_mitochodrial_transport': '2034', # name="pyruvate transport" id="R_2034"
  '1.2.4.1': '961', # name="pyruvate dehydrogenase" id="R_961"
  '1.2.4.1_2': '-', # pyruvate dehydrogenase (lipoamide)
  '2.3.1.12': '-', # pyruvate dehydrogenase (dihydrolipoamide) reversible (mitochondrial) 
  '2.3.3.1': '300', # citrate synthase (mitochondrial) id="R_300"
  '4.2.1.3': '2305', # aconitase (mitochondrial) name="cis-aconitate(3-) to isocitrate" id="R_2305" (?)
  '1.1.1.41': '658', # isocitrate dehydrogenase (NAD+) id="R_658"
  '1.2.4.2': '832', # name="oxoglutarate dehydrogenase (lipoamide)" id="R_832"
  '1.2.4.2_2': '-', # 
  '2.3.1.61': '831', # oxoglutarate dehydrogenase (dihydrolipoamide S-succinyltransferase) id="R_831"
  '6.2.1.4': '1022', # succinate-CoA ligase (ADP-forming)" id="R_1022" 
  '6.2.1.5': '668', # name="itaconate-CoA ligase (ADP-forming)" id="R_668" (?)
  '1.3.5.1': '1021', # succinate dehydrogenase (ubiquinone-6) (m) id="R_1021"
  '4.2.1.2': '451', # fumarase (mitochondrial) id="R_451"
}

# iYLI647
iYli647_citrate_cycle = {
  '6.4.1.1': 'PC', # (id:R_PC) pyruvate carboxylase (Pyruvate -> Oxaloacetate)
  '1.1.1.37': 'MDHm', # (id:R_MDHm) malate dehydrogenase, mitochondrial (Malate -> Oxaloacetate)  
  'pyruvate_mitochodrial_transport': 'PYRt2m', # id="R_PYRt2m" name="pyruvate mitochondrial transport via proton symport" Pyruvate c -> pyruvate mito
  '1.2.4.1': 'PDHm', # pyruvate dehydrogenase id="R_PDHm"
  '1.2.4.1_2': '-', # pyruvate dehydrogenase (lipoamide)
  '2.3.1.12': '-', # pyruvate dehydrogenase (dihydrolipoamide) reversible (mitochondrial) 
  '2.3.3.1': 'CSm', # citrate synthase (mitochondrial) id="R_CSm"
  '4.2.1.3': 'ACONT', # aconitase (mitochondrial) id="R_ACONT"
  '1.1.1.41': 'ICDHxm', # isocitrate dehydrogenase (NAD+) id="R_ICDHxm"
  '1.2.4.2_1': 'AKGDam', # 2-oxoglutarate dehydrogenase id="R_AKGDam" name="oxoglutarate dehydrogenase lipoamide"
  '1.2.4.2_2': '-', # 2-oxoglutarate dehydrogenase 
  '2.3.1.61': 'AKGDbm', # oxoglutarate dehydrogenase dihydrolipoamide S succinyltransferase id="R_AKGDbm" (mitochondrial)
  '6.2.1.4': 'SUCOASm', # Succinate--CoA ligase (GDP-forming)
  '6.2.1.5': 'ITCOALm', # Itaconate CoA ligase ADP forming mitochondrial id="R_ITCOALm" (?)
  '1.3.5.1': 'SUCD2_u6m', # succinate dehydrogenase ubiquinone 6 mitochondrial id="R_SUCD3_u6m"
  '4.2.1.2': 'FUMm', # fumarase mitochondrial id="R_FUMm"
}



In [19]:
def get_fva_flux_table(model_name, fluxes, fva_intervals, reaction_table):
    """Returns a pandas dataframe with fluxes and their corresponding fva intervals."""
    # fluxes to dataframe and key as column
    flux_df = pd.DataFrame.from_dict(fluxes, orient='index', columns=['flux', 'reaction_id'])
    # index to column with name EC
    flux_df.reset_index(inplace=True)
    flux_df.columns = ['EC', f'{model_name}_flux', f'{model_name}_reaction_id']

    # fva_intervals to dataframe
    fva_intervals = pd.DataFrame.from_dict(fva_intervals, orient='index', columns=['min', 'max'])
    # index to column with name EC
    fva_intervals.reset_index(inplace=True)
    fva_intervals.columns = ['EC', f'{model_name}_min', f'{model_name}_max']

    # left join flux_df to glycolysis table on EC
    glycolysis_result = pd.merge(pd.merge(reaction_table, flux_df, on='EC', how='left'), fva_intervals, on='EC', how='left')
    return glycolysis_result
    

In [22]:
# merge iMT1026v3_glycolysis_without_branches and iMT1026v3_citrate_cycle
iMT1026v3_glycolysis_and_citrate_cycle = {**iMT1026v3_glycolysis_without_branches, **iMT1026v3_citrate_cycle}
iMT1026v3_glycolysis_and_citrate_cycle

# merge iYLI647_glycolysis_without_branches and iYLI647_citrate_cycle
yli647_glycolysis_and_citrate_cycle = {**iYli647_glycolysis_without_branches, **iYli647_citrate_cycle}
yli647_glycolysis_and_citrate_cycle

# merge iYali4_glycolysis_without_branches and yali4_citrate_cycle
yali4_glycolysis_and_citrate_cycle = {**iYali4_glycolysis_without_branches, **iYali4_citrate_cycle}
yali4_glycolysis_and_citrate_cycle


{'2.7.1.1': '534',
 '5.3.1.9': '467',
 '2.7.1.11': '886',
 '4.1.2.13': '450',
 '4.1.2.13b': '450',
 '5.3.1.1': '1054',
 '1.2.1.12': '486',
 '2.7.2.3': '892',
 '5.4.2.11': '893',
 '4.2.1.11': '366',
 '2.7.1.40': '962',
 '6.4.1.1': '958',
 '1.1.1.37': '713',
 'pyruvate_mitochodrial_transport': '2034',
 '1.2.4.1': '961',
 '1.2.4.1_2': '-',
 '2.3.1.12': '-',
 '2.3.3.1': '300',
 '4.2.1.3': '2305',
 '1.1.1.41': '658',
 '1.2.4.2': '832',
 '1.2.4.2_2': '-',
 '2.3.1.61': '831',
 '6.2.1.4': '1022',
 '6.2.1.5': '668',
 '1.3.5.1': '1021',
 '4.2.1.2': '451'}

In [22]:
# get flux and fva table for glycolysis, citrate cycle 
# iMT1026v3_citrate_cycle, iYli21_citrate_cycle
# load EC, reaction table with pandas
reaction_table = pd.read_csv('../' +config['experiments']['reaction_table'], sep=config['seperator'])
_loopless = True
_verbose = False
_condition = 'loopless_true_last_test_all_glycolysis_TCA'

# iYali4 results
model_name = 'iYali4'
print(f"{model_name}: \n")
biomass_rxn = 'biomass_C'
maintenance_rxn = 'xMAINTENANCE'
growth_condition = {
    '1714': 100, # glucose
    '1709': 0, # fructose
    '1808': 0, # glycerol
}

# For glycolysis and citrate cycle
iYali4_glycolysis_and_citrate_cycle = {**iYali4_glycolysis_without_branches, **iYali4_citrate_cycle}

current_fluxes = get_reaction_fluxes(iYali4_model, iYali4_glycolysis_and_citrate_cycle, biomass_rxn, growth_condition, maintenance_rxn, _yli_maintenance)
iYali4_fva_solution, current_fva_intervals = get_fva_intervals(iYali4_model, iYali4_glycolysis_and_citrate_cycle, biomass_rxn, growth_condition, maintenance_rxn, _yli_maintenance, _loopless, "", _verbose)
# add both to the csv table
reaction_table = get_fva_flux_table(model_name, current_fluxes, current_fva_intervals, reaction_table)
reaction_table.to_csv(f"{'../' +config['results']['metabolic_fluxes']}/{_condition}_flux_fva.csv", sep=config['seperator'], index=False)

# iYli647 results
model_name = "iYLI647"
print(f"{model_name}: \n")
biomass_rxn = 'biomass_C'
maintenance_rxn = 'ATPM'
growth_condition = {
    'EX_glc(e)': 100, # glucose
    'EX_fru(e)': 0, # fructose
    'EX_glyc(e)': 0, # glycerol
}

# For glycolysis and citrate cycle
iYli647_glycolysis_and_citrate_cycle = {**iYli647_glycolysis_without_branches, **iYli647_citrate_cycle}

current_fluxes = get_reaction_fluxes(iYli647_model, iYli647_glycolysis_and_citrate_cycle, biomass_rxn, growth_condition, maintenance_rxn, _yli_maintenance)
iYli647_fva_solution, current_fva_intervals = get_fva_intervals(iYli647_model, iYli647_glycolysis_and_citrate_cycle, biomass_rxn, growth_condition, maintenance_rxn, _yli_maintenance, _loopless, "", _verbose)
# add both to the csv table
reaction_table = get_fva_flux_table(model_name, current_fluxes, current_fva_intervals, reaction_table)
reaction_table.to_csv(f"{'../' +config['results']['metabolic_fluxes']}/{_condition}_flux_fva.csv", sep=config['seperator'], index=False)

# # iMT1026v3 results
model_name = 'iMT1026v3'
print(f"{model_name}: \n")
biomass_rxn = 'growth' # BIOMASS_glyc # (id:BIOMASS) Biomass composition # growth biomass_c --> biomass_e
maintenance_rxn = 'ATPM' # 0.55 
growth_condition = {
    'Ex_glc_D': 100, # glucose
    'Ex_fru': 0, # fructose
    'Ex_glyc': 0, # glycerol
    'Ex_o2': 1000, # O2
}

# For glycolysis and citrate cycle
iMT1026v3_glycolysis_and_citrate_cycle = {**iMT1026v3_glycolysis_without_branches, **iMT1026v3_citrate_cycle}
# fluxes and fva intervals
current_fluxes = get_reaction_fluxes(iMT1026v3_model, iMT1026v3_glycolysis_and_citrate_cycle, biomass_rxn, growth_condition, maintenance_rxn, _ppa_maintenance)
iMT1026v3_fva_solution, current_fva_intervals = get_fva_intervals(iMT1026v3_model, iMT1026v3_glycolysis_and_citrate_cycle, biomass_rxn, growth_condition, maintenance_rxn, _ppa_maintenance, _loopless, "", _verbose)
# get flux table
reaction_table = get_fva_flux_table(model_name, current_fluxes, current_fva_intervals, reaction_table)
# output
# reaction_table.to_csv(f"{config['results']['metabolic_fluxes']}/{_condition}_flux_fva.csv", sep=config['seperator'], index=False)

# # iLC915 results
# model_name = 'iLC915'
# print(f"{model_name}: \n")
# biomass_rxn = 'r1339' # r1339 Growth # r1187 biomass formation
# maintenance_rxn = 'r1188' # Maintenance
# growth_condition = {
#     'r1145': 100, # glucose
#     'r1144': 0, # fructose
#     'r1148': 0, # glycerol
#     'r1160': 1000, # O2
# }

# # For glycolysis and citrate cycle
# iLC915_glycolysis_and_citrate_cycle = {**iLC915_glycolysis_without_branches, **iLC915_citrate_cycle}
# # fluxes and fva intervals
# current_fluxes = get_reaction_fluxes(iLC915_model, iLC915_glycolysis_and_citrate_cycle, biomass_rxn, growth_condition, maintenance_rxn, _ppa_maintenance)
# iLC915_fva_solution, current_fva_intervals = get_fva_intervals(iLC915_model, iLC915_glycolysis_and_citrate_cycle, biomass_rxn, growth_condition, maintenance_rxn, _ppa_maintenance, _loopless, "", _verbose)
# # get flux table
# reaction_table = get_fva_flux_table(model_name, current_fluxes, current_fva_intervals, reaction_table)
# # output
# # reaction_table.to_csv(f"{config['results']['metabolic_fluxes']}/{_condition}_flux_fva.csv", sep=config['seperator'], index=False)

# iYli21 results
model_name = 'iYli21'
print(f"{model_name}: \n")
biomass_rxn = 'biomass_C'
maintenance_rxn = 'xMAINTENANCE'
growth_condition = {
    'R1070': 100, # glucose
    'R1065': 0, # fructose
    'R1141': 0, # glycerol
}
# For glycolysis and citrate cycle
iYli21_glycolysis_and_citrate_cycle = {**iYli21_glycolysis_without_branches, **iYli21_citrate_cycle}

current_fluxes = get_reaction_fluxes(iYli21_model, iYli21_glycolysis_and_citrate_cycle, biomass_rxn, growth_condition, maintenance_rxn, _yli_maintenance)
iYli21_fva_solution, current_fva_intervals = get_fva_intervals(iYli21_model, iYli21_glycolysis_and_citrate_cycle, biomass_rxn, growth_condition, maintenance_rxn, _yli_maintenance, _loopless, "", _verbose)
# add both to the csv table
reaction_table = get_fva_flux_table(model_name, current_fluxes, current_fva_intervals, reaction_table)
reaction_table.to_csv(f"{'../' +config['results']['metabolic_fluxes']}/{_condition}_flux_fva.csv", sep=config['seperator'], index=False)

# without loopless=True
# for iMT1026v3: 22 seconds
# for iYli21: 21 second

# with loopless=True
# for iMT1026v3: 7min
# for iYli21: 7min




iYali4: 

iYLI647: 

iMT1026v3: 



/Users/ampholyt/Coding/BSEP22/Code/With_Bockmayr/EFM_calculation_cobamp/venv/lib/python3.8/site-packages/cobra/util/solver.py:554: UserWarning: Solver status is 'infeasible'.
  warn(f"Solver status is '{status}'.", UserWarning)
/Users/ampholyt/Coding/BSEP22/Code/With_Bockmayr/EFM_calculation_cobamp/venv/lib/python3.8/site-packages/cobra/util/solver.py:554: UserWarning: Solver status is 'infeasible'.
  warn(f"Solver status is '{status}'.", UserWarning)
/Users/ampholyt/Coding/BSEP22/Code/With_Bockmayr/EFM_calculation_cobamp/venv/lib/python3.8/site-packages/cobra/util/solver.py:554: UserWarning: Solver status is 'infeasible'.
  warn(f"Solver status is '{status}'.", UserWarning)
/Users/ampholyt/Coding/BSEP22/Code/With_Bockmayr/EFM_calculation_cobamp/venv/lib/python3.8/site-packages/cobra/util/solver.py:554: UserWarning: Solver status is 'infeasible'.
  warn(f"Solver status is '{status}'.", UserWarning)


iYli21: 



/Users/ampholyt/Coding/BSEP22/Code/With_Bockmayr/EFM_calculation_cobamp/venv/lib/python3.8/site-packages/cobra/util/solver.py:554: UserWarning: Solver status is 'infeasible'.
  warn(f"Solver status is '{status}'.", UserWarning)


In [23]:
# iLC915 results
model_name = 'iLC915'
print(f"{model_name}: \n")
biomass_rxn = 'r1339' # r1339 Growth # r1187 biomass formation
maintenance_rxn = 'r1188' # Maintenance
growth_condition = {
    'r1145': 100, # glucose
    'r1144': 0, # fructose
    'r1148': 0, # glycerol
    'r1160': 1000, # O2
}

# fluxes and fva intervals
current_fluxes = get_reaction_fluxes(iLC915_model, iLC915_glycolysis_without_branches, biomass_rxn, growth_condition, maintenance_rxn, _ppa_maintenance)
iLC915_fva_solution, current_fva_intervals = get_fva_intervals(iLC915_model, iLC915_glycolysis_without_branches, biomass_rxn, growth_condition, maintenance_rxn, _ppa_maintenance, _loopless, "", _verbose)
# get flux table
reaction_table = get_fva_flux_table(model_name, current_fluxes, current_fva_intervals, reaction_table)
# output
reaction_table.to_csv(f"{config['results']['metabolic_fluxes']}/{_condition}_flux_fva.csv", sep=config['seperator'], index=False)


iLC915: 



FileNotFoundError: [Errno 2] No such file or directory: '../results/FBA_results/metabolic_fluxes/loopless_true_last_test_all_glycolysis_TCA_flux_fva.csv'

In [27]:

reaction_table.to_csv(f"../{config['results']['metabolic_comparison_condition']}", sep=config['seperator'], index=False)


In [20]:
# check error of iYli647
iYli647_glycolysis_and_citrate_cycle

{'2.7.1.1': 'HEX1',
 '5.3.1.9': 'PGI',
 '2.7.1.11': 'PFK',
 '4.1.2.13': 'FBA',
 '5.3.1.1': 'TPI',
 '1.2.1.12': 'GAPD',
 '2.7.2.3': 'PGK',
 '5.4.2.11': 'PGM',
 '4.2.1.11': 'ENO',
 '2.7.1.40': 'PYK',
 '6.4.1.1': 'PC',
 '1.1.1.37': 'MDHm',
 'pyruvate_mitochodrial_transport': 'r1291',
 '1.2.4.1': 'PDHm',
 '1.2.4.1_2': '-',
 '2.3.1.12': '-',
 '2.3.3.1': 'CSm',
 '4.2.1.3': 'ACONT',
 '1.1.1.41': 'ICDHxm',
 '1.2.4.2_1': 'AKGDam',
 '1.2.4.2_2': '-',
 '2.3.1.61': 'AKGDbm',
 '6.2.1.4': 'SUCOASm',
 '6.2.1.5': 'ITCOALm',
 '1.3.5.1': 'SUCD2_u6m',
 '4.2.1.2': 'FUMm'}

## Check alternative pathways
- Glycolysis:
    - iMT1026v3: Hexokinase and glucose-6-phosphate isomerase
    - All: 4.1.2.13
- TCA cycle:
    - Alle: Citrate -> Isocitrate 
    - iYli21: Isocitrate -> Alpha-Keto-gluterate
    - iMT1026v3: Succinate -> Fumerate
    - iMT1026v3: Fumerate -> Malate


In [17]:
iMT1026v3_glycolysis_without_branches = {
    "2.7.1.1": "HEX1", # id="R_HEX1" name="hexokinase (D-glucose:ATP)"
    "5.3.1.9": "PGI", # id="R_PGI" name="glucose-6-phosphate isomerase"
    "5.1.3.3(a-D-g->b-D-g6p)": "GLUK", # +2.7.1.1 a-D-g -> b-D-g6p id="R_GLUK" Alternative pathway from glucose to fructose-6-phosphate
    "5.1.3.9(b-D-g6P<=>b-D-f6P)": "G6PI3", # id="R_G6PI3" name="glucose-6-phosphate isomerase (b-D-glucose-6P <=> b-D-fructose-6P)"
    "5.1.3.9(g6p_c<=>g6p_B_c)": "G6PI", # id="R_G6PI" name="glucose-6-phosphate isomerase (g6p_c <=> g6p_B_c)"
    "1.1.1.49(gly->ppp)": "G6PDH2", # id="G6PDH2" name="glucose 6-phosphate dehydrogenase" g6p -> PPP
    "5.1.3.1(ru5p_D_c<=>xu5p_D_c)": "RPE", # id="RPE" name="ribulose 5-phosphate 3-epimerase" ru5p_D_c <=> xu5p_D_c
    "2.2.1.1(ppp->gly)": "TKT2", # id="TKT2" name="transketolase" PPP from ppp -> f6p + g3p
    "2.7.1.11": "PFK", # id="R_PFK" name="phosphofructokinase"
    "4.1.2.13": "FBA", # id="R_FBA" name="fructose-bisphosphate aldolase"
    "4.1.2.13b": "FBA2", # id="R_FBA2" name="D-Fructose 1-phosphate D-glyceraldehyde-3-phosphate-lyase" (alternative zu FBA)
    "5.3.1.1": "TPI", # id="R_TPI" name="triose-phosphate isomerase"
    "1.2.1.12": "GAPD", # id="R_GAPD" name="glyceraldehyde-3-phosphate dehydrogenase"
    "2.7.2.3": "PGK", # id="R_PGK" name="phosphoglycerate kinase"
    "5.4.2.11": "PGM", # id="R_PGM" name="phosphoglycerate mutase" # iMT1026v3: EC: 5.4.2.1
    "4.2.1.11": "ENO", # id="R_ENO" name="enolase"
    "2.7.1.40": "PYK",# id="R_PYK" name="pyruvate kinase" 
}

In [44]:
# find alternative to hexokinase 
hex1 = iMT1026v3_model.reactions.get_by_id('HEX1')
hex1
g6p_c = iMT1026v3_model.metabolites.get_by_id('g6p_c')
g6p_c.summary()

In [13]:
fru_sol # G6PI3	g6p_B_c <=> f6p_c
        # TKT2	e4p_c + xu5p_D_c <=> f6p_c + g3p_c

In [15]:
# g6p_B_c
G6PI = iMT1026v3_model.reactions.get_by_id('G6PI')
G6PI

<Reaction G6PI at 0x2a73c5ac0>

In [36]:
# find ru5p_D_c in imt1026v3
# ru5p_D_c = iMT1026v3_model.metabolites.get_by_id('ru5p_D_c')
# ru5p_D_c

# xu5p_D_c = iMT1026v3_model.metabolites.get_by_id('xu5p_D_c')
# xu5p_D_c #D-Xylulose 5-phosphate

 
# # find D-Ribulose 5-phosphate in yli21 # m96[c] D-ribulose 5-phosphate_C5H11O8P
# for met in iYli21_model.metabolites:
#     if 'ribulose' in met.name.lower():
#         print(met.id, met.name)

# # find D-Xylulose 5-phosphate in yli21 # m938[c] D-xylulose 5-phosphate_C5H11O8P
# for met in iYli21_model.metabolites:
#     if 'xylulose' in met.name.lower(): 
#         print(met.id, met.name)

# # m938[c]
# iYli21_model.metabolites.get_by_id('m938[c]').summary()
R714 = iYli21_model.reactions.get_by_id('R714')
R714

# # m96[c]
# iYli21_model.metabolites.get_by_id('m96[c]').summary()

# # R639 = iYli21_model.reactions.get_by_id('R639')
# # R639

# R712 = iYli21_model.reactions.get_by_id('R712')
# R712

<Reaction R714 at 0x2a8665820>

In [22]:
# start with iMT1026v3 
_loopless = True
_verbose = False
model_name = 'iMT1026v3'
print(f"{model_name}: \n")
biomass_rxn = 'growth' # BIOMASS_glyc # (id:BIOMASS) Biomass composition # growth biomass_c --> biomass_e
maintenance_rxn = 'ATPM' # 0.55 
growth_condition = {
    'Ex_glc_D': 100, # glucose
    'Ex_fru': 0, # fructose
    'Ex_glyc': 0, # glycerol
    'Ex_o2': 1000, # O2
}
# ## set growth condition to glucose
set_growth_condition(iMT1026v3_model, biomass_rxn, growth_condition, maintenance_rxn, _ppa_maintenance)

# # get reactions for glycolysis:
# iMT1026v3_glycolysis_without_branches
# # HEX1: Glucose -> Glucose 6-phosphate
# hex1 = iMT1026v3_model.reactions.get_by_id('HEX1')
# # analyse production of g6p_c
# iMT1026v3_model.metabolites.get_by_id('g6p_c').summary(fva=0.95) # 100% HEX1 if grown on glucose according to FBA solution

# # sanity check of the results: => alternative pathway for glucose production
# iMT1026v3_fva_solution, iMT1026v3_current_fva_intervals = get_fva_intervals(iMT1026v3_model, iMT1026v3_glycolysis_without_branches, biomass_rxn, growth_condition, maintenance_rxn, _ppa_maintenance, _loopless, "", _verbose)

# # How is Fructose-6-phosphate produced?
with iMT1026v3_model as model:
#     # # knockout: PGI => production through G6PI3: g6p_B_c <=> f6p_c
    # model.reactions.get_by_id('PGI').bounds = (0,0)
    # model.reactions.get_by_id('G6PI3').bounds = (0,0)
    model.reactions.get_by_id('G6PI').bounds = (0,0)

    # model.reactions.get_by_id('GLUK').bounds = (0,0)
    model.reactions.get_by_id('HEX1').bounds = (0,0)
    g6p_c = model.metabolites.get_by_id('g6p_c')
    g6p_c_sol = g6p_c.summary() # G6PI	g6p_c <=> g6p_B_c
    # g6p_B_c = model.metabolites.get_by_id('g6p_B_c')
    # g6p_B_c = g6p_B_c.summary()
    # f6p_c = model.metabolites.get_by_id('f6p_c')
    # # fru_c = model.metabolites.get_by_id('fru_c')
    # fru_sol = f6p_c.summary()
    # sol = f6p_c.summary() # GLUK: atp_c + glc_D_c --> adp_c + g6p_B_c + h_c
g6p_c_sol
# sol
# TKT2 = iMT1026v3_model.reactions.get_by_id('TKT2')
# TKT2 # e4p_c + xu5p_D_c <=> f6p_c + g3p_c
# xu5p_D_c = iMT1026v3_model.metabolites.get_by_id('xu5p_D_c')
# xu5p_D_c.summary() # ru5p_D_c <=> xu5p_D_c
# ru5p_D_c = iMT1026v3_model.metabolites.get_by_id('ru5p_D_c')
# ru5p_D_c.summary() # GND: 6pgc_c + nadp_c --> co2_c + nadph_c + ru5p_D_c
# iMT1026v3_model.metabolites.get_by_id('6pgc_c').summary() #PGL: 6pgl_c + h2o_c --> 6pgc_c + h_c

# iMT1026v3_model.metabolites.get_by_id('6pgl_c').summary() # G6PDH2	g6p_c + nadp_c --> 6pgl_c + h_c + nadph_c
# G6PDH2 = iMT1026v3_model.reactions.get_by_id('G6PDH2')
# G6PDH2 # glucose 6-phosphate dehydrogenase g6p_c + nadp_c --> 6pgl_c + h_c + nadph_c
# iMT1026v3_current_fva_intervals

iMT1026v3: 



In [21]:
iMT1026v3_current_fva_intervals # => finde die alternativ Reaktionen


{'2.7.1.1': (0.0, 99.99999999999221),
 '5.3.1.9': (0.0, 39.27624013471325),
 '5.1.3.3(a-D-g -> b-D-g6p)': (0.0, 99.99999999999172),
 '5.1.3.9(b-D-g6P<=>b-D-f6P)': (0.0, 39.27624013546756),
 '5.1.3.9(g6p_c<=>g6p_B_c)': (0.0, 0.0),
 '1.1.1.49(gly->ppp)': (39.86610429491922, 39.866104294841755),
 '5.1.3.1(ru5p_D_c<=>xu5p_D_c)': (22.79898852617614, 22.799000423270698),
 '2.2.1.1(ppp->gly)': (9.947911171336138, 9.947911171322827),
 '2.7.1.11': (43.945778554925795, 43.94577855488333),
 '4.1.2.13': (-3.349498456373112e-11, 43.945778554998356),
 '4.1.2.13b': (3.822719918389339e-12, 0.0),
 '5.3.1.1': (56.596166879402446, 56.596166878834154),
 '1.2.1.12': (123.81374257589798, 123.81374257637825),
 '2.7.2.3': (-123.81374257645672, -123.81374257660457),
 '5.4.2.11': (-115.31283857979872, -115.31283857976294),
 '4.2.1.11': (115.31283857989465, 115.31283857982227),
 '2.7.1.40': (109.50650621284235, 109.50650621282495)}

#### iYli21 + iYali4 and new glycolysis

In [38]:
# # iYli21 results
# model_name = 'iYli21'
# print(f"{model_name}: \n")
# biomass_rxn = 'biomass_C'
# maintenance_rxn = 'xMAINTENANCE'
# growth_condition = {
#     'R1070': 100, # glucose
#     'R1065': 0, # fructose
#     'R1141': 0, # glycerol
# }

# iYli21_fva_solution, iYli21_current_fva_intervals = get_fva_intervals(iYli21_model, iYli21_glycolysis_without_branches, biomass_rxn, growth_condition, maintenance_rxn, _ppa_maintenance, _loopless, "", _verbose)

# # iYali4 results
# model_name = 'iYali4'
# print(f"{model_name}: \n")
# biomass_rxn = 'biomass_C'
# maintenance_rxn = 'xMAINTENANCE'
# growth_condition = {
#     '1714': 100, # glucose
#     '1709': 0, # fructose
#     '1808': 0, # glycerol
# }

# iYali4_fva_solution, iYali4_current_fva_intervals = get_fva_intervals(iYali4_model, iYali4_glycolysis_without_branches, biomass_rxn, growth_condition, maintenance_rxn, _yli_maintenance, _loopless, "", _verbose)


iYli21: 



/Users/ampholyt/Coding/BSEP22/Code/With_Bockmayr/EFM_calculation_cobamp/venv/lib/python3.8/site-packages/cobra/util/solver.py:554: UserWarning: Solver status is 'infeasible'.
  warn(f"Solver status is '{status}'.", UserWarning)


In [39]:
iYli21_current_fva_intervals

{'2.7.1.1': (99.99999999999888, 100.0000000000191),
 '5.3.1.9': (46.719471586166236, 46.719471586125366),
 '2.7.1.11': (42.259837860943094, 42.259837860851306),
 'ppp->ppp': (-828.824940170512, 23.22703903306893),
 '4.1.2.13': (42.25983786093997, 42.259837860959806),
 '4.1.2.13b': (42.25983786093997, 42.259837860959806),
 '5.3.1.1': (54.70025941629822, 54.727387438181346),
 '1.2.1.12': (120.24392613853342, 120.24392613859357),
 '2.7.2.3': (120.24392613857546, 120.2439261385952),
 '5.4.2.11': (110.78362755642056, 110.78362755642095),
 '4.2.1.11': (110.78362755647231, 110.78362755645594),
 '2.7.1.40': (107.31325126947289, 107.31325126952504)}

In [ ]:
iYali4_current_fva_intervals

## Start introducing iLC915 in final plot as well (do not follow this now: no EC values and different nameing)

In [55]:
# get current result for iLC915 on glycolysis (do I need to find alternatives as well?)
_loopless = True
# iLC915 results
model_name = 'iLC915'
print(f"{model_name}: \n")
biomass_rxn = 'r1339' # r1339 Growth # r1187 biomass formation
maintenance_rxn = 'r1188' # Maintenance
growth_condition = {
    'r1145': 100, # glucose
    'r1144': 0, # fructose
    'r1148': 0, # glycerol
    'r1160': 1000, # O2
}

iLC915_fva_solution, iLC915_current_fva_intervals = get_fva_intervals(iLC915_model, iLC915_glycolysis_without_branches, biomass_rxn, growth_condition, maintenance_rxn, _ppa_maintenance, _loopless, "", _verbose)


iLC915: 



In [56]:
iLC915_current_fva_intervals

{'2.7.1.1': (0.0, 1000.0),
 '5.3.1.9': (-540.4893025881616, 852.2230262036442),
 'PPP->glycer3p': (-609.4662849908176, 190.17387918045057),
 '2.7.1.11': (0.0, 651.0496283533796),
 '4.1.2.13': (-6.602007829314971e-11, 651.0496283530589),
 '5.3.1.1': (-828.2067309671028, -428.38664888115704),
 '1.2.1.12': (1000.0000000000757, 1000.0),
 '2.7.2.3': (-1000.0, -999.9999999999043),
 '5.4.2.11': (-1000.0, -1000.0000000003818),
 '4.2.1.11': (1000.0000000005073, 1000.0),
 '2.7.1.40': (1000.0000000001814, 1000.0)}

In [53]:
# # find ribulose 5-phosphate in iLC915 # m143 D-Ribulose 5-phosphate_C5H11O8P
# for met in iLC915_model.metabolites:
#     if 'ribulose' in met.name.lower():
#         print(met.id, met.name)

# m143 = iLC915_model.metabolites.get_by_id('m143')
# m143.summary()
# # find ribose 
# # for met in iLC915_model.metabolites: #m144 D-Ribose 5-phosphate_C5H11O8P
# #     if 'ribose' in met.name.lower():
# #         print(met.id, met.name)

# m144 = iLC915_model.metabolites.get_by_id('m144')
# m144.summary()
# # r974	m143 <=> m149
# r974 = iLC915_model.reactions.get_by_id('r974') # D-Ribulose-5-phosphate 3-epimerase
# r974 # D-Ribulose 5-phosphate_C5H11O8P <=> D-Xylulose 5-phosphate_C5H11O8P
# # m149 # D-Xylulose 5-phosphate_C5H11O8P
# with iLC915_model as model:
#     # model.reactions.get_by_id('r974').bounds = (0,0)
#     m143 = model.metabolites.get_by_id('m143')
#     m149 = model.metabolites.get_by_id('m149')
#     m143_sol = m143.summary()
#     m149_sol = m149.summary()
# print(m143_sol)
# m149_sol
# find glyceraldehyde 3-phosphate
for met in iLC915_model.metabolites: # m12 D-Glyceraldehyde 3-phosphate_C3H7O6P
    if 'glyceraldehyde' in met.name.lower():
        print(met.id, met.name)

m12 = iLC915_model.metabolites.get_by_id('m12')
m12.summary()

r319 = iLC915_model.reactions.get_by_id('r319') # D-Glyceraldehyde-3-phosphate dehydrogenase
r319 # m12 + m13 + m14 <=> m15 + m16


m12 D-Glyceraldehyde 3-phosphate_C3H7O6P
m702 D-Glyceraldehyde_C3H6O3
m959 D-Glyceraldehyde 3-phosphate_C3H7O6P


<Reaction r319 at 0x28f539970>

In [19]:
current_fva_intervals

{'2.7.1.1': (99.99999999999596, 100.0),
 '5.3.1.9': (81.08541857432851, 81.08541856585065),
 '2.7.1.11': (71.1230892310207, 71.12308922893214),
 '4.1.2.13': (71.12308923089984, 71.1230892310361),
 '5.3.1.1': (-73.33233953331414, -73.33233953323756),
 '1.2.1.12': (149.3312141916587, 149.33121419165587),
 '2.7.2.3': (-149.33121419165744, -149.33121419095187),
 '5.4.2.11': (-129.88686353108605, -129.88686353179503),
 '4.2.1.11': (129.8868635321181, 129.8868635325432),
 '2.7.1.40': (125.36865676242306, 125.3686567643928)}

In [257]:
### Investigate what the growth condition of iMT1026v3 is
iMT1026v3_model.summary() # all good but biotine is used as well
# # check range of biotine uptake
# iMT1026v3_fva_solution.loc['Ex_btn'] # min: -0.000012 max -0.000012
# # check glucose uptake and usage
# iMT1026v3_model.metabolites.glc_D_e.summary() # ext -> cyt 100 
# iMT1026v3_model.metabolites.glc_D_c.summary() # cyt -> cyt 39: GLUK; 61: HEX1
# # check GLUK 
# iMT1026v3_model.reactions.GLUK # ATP + D-Glucose --> ADP + beta-D-glucose 6-phosphate + H+ (atp_c + glc_D_c --> adp_c + g6p_B_c + h_c)
# iMT1026v3_model.reactions.HEX1 # ATP + D-Glucose --> ADP + alpha-D-Glucose 6-phosphate + H+ (atp_c + glc_D_c --> adp_c + g6p_c + h_c)
# # check how beta glucose is used in iMT1026v3
# iMT1026v3_model.metabolites.g6p_B_c.summary() # 100 -> f6p_c
# iMT1026v3_model.metabolites.g6p_c.summary() # 40 -> G6PDH2; 20 -> PGMT (g1p_c)

# # check PGI glucose 6-phosphate isomerase
# iMT1026v3_model.reactions.PGI.summary() # G6P <=> F6P (g6p_c <=> f6p_c)
# iMT1026v3_model.reactions.get_by_id('PGI') # g6p_c <=> f6p_c
# iMT1026v3_model.metabolites.g6p_c.summary() # no PGI
# # how is f6p_c produced?
iMT1026v3_model.metabolites.f6p_c.summary() 
# #### from beta-D-glucose 6-phosphate (g6p_B_c) (80%)
# #### consumed: PFK (6-phosphofructokinase) (89%)
# # compare to iYali4
# iYali4_model.summary() # all good
# # check m1031 
# iYali4_model.metabolites.m1031 # ammonium

### Investigate Differences in the model:
#### iMT1026v3
- HEX1 is optional
- Glucose-6-Phosphate -> Fructose 6-phosphate
- Fructose-1,6-bisphosphate -> Dihydroxyacetone phosphate
- Citrate -> isocitrate optional
- Succinate -> Fumerate optional
- Fumerate -> Malate infeasible flux range (?)

#### iYli21
- Fructose-1,6-Bisphosphate -> Dihydroxyacetone phosphate
- Citrate -> Isocitrate (optional)
- Isocitrate -> Alphaketogluterate (Zero flux)

#### iYali4
- Fructose-1,6-Bisphosphate -> Dihydroxyacetone phosphate
- Citrate -> Isocitrate (optional)
- Isocitrate -> Alphaketogluterate (infeasible flux range (?))


In [132]:
# which possibilities are incorporated for glucose degradation in iYali4: 534, 467
# iYali4_model.summary()

# r534 = iYali4_model.reactions.get_by_id('534') # hex: ATP[cy] + D-glucose[cy] --> H+_p+1[cy] + ADP[cy] + D-glucose 6-phosphate[cy]: m141 + m295 --> m10 + m143 + m296
# r534
# #alternative usages of glucose
# m295 = iYali4_model.metabolites.get_by_id('m295') # D-glucose[e]
# m295.summary() # 100 -> 534; 100 -> 467
# block reaction 534
# r534.bounds = (0,0)
# iYali4_model.summary() # no growth => there is no alternative to the 543 reaction


# r467 = iYali4_model.reactions.get_by_id('467') # glucose-6-phosphate isomerase: D-glucose 6-phosphate[cy] <=> D-fructose 6-phosphate[cy]
# r467
#find glucokinase in iYali4 (all reactions using flucose)
# for rxn in m295.reactions:
#     print(rxn.id, rxn.name, rxn.reaction) # m295: cytosolic glucose, m511: extracelular glucose

# # # investigate if iYli21 also have only one hexokinase
# # iYli21_model.summary() # all good
# m511 = iYli21_model.metabolites.get_by_id('m511[e]') # m511: extracelular glucose
# m511
# # # iterate reactions
# for rxn in m511.reactions: # m295[c]: cytosolic glucose
#     print(rxn.id, rxn.name, rxn.reaction, hf.formulaWithNames(rxn))
# m295 = iYli21_model.metabolites.get_by_id('m295[c]') # m295: cytosolic glucose
# for rxn in m295.reactions: # m295[c]: cytosolic glucose
#     print(rxn.id, rxn.name, rxn.reaction, hf.formulaWithNames(rxn))

# # investigate S. cerevisiae
# scere = cobra.io.read_sbml_model(config['models']['scere'])
# scere.summary() # all good
# # check usage of glucose
# glc__D_e = scere.metabolites.get_by_id('glc__D_e') # extracellular glucose
# # glc__D_e.summary() # consumed: 100% GLCt1
# for rxn in glc__D_e.reactions: # glc__D_c: cytosolic glucose
#     print(rxn.id, rxn.name, rxn.reaction, hf.formulaWithNames(rxn))

# for rxn in scere.metabolites.get_by_id('glc__D_c').reactions:
#     print(rxn.id, rxn.name, rxn.reaction, hf.formulaWithNames(rxn))

# GLUK Glucokinase atp_c + glc__D_c --> adp_c + g6p_B_c + h_c ATP C10H12N5O13P3 + D-Glucose --> ADP C10H12N5O10P2 + Beta D glucose 6 phosphate C6H11O9P + H+
# HEX1 Hexokinase (D-glucose:ATP) atp_c + glc__D_c --> adp_c + g6p_c + h_c ATP C10H12N5O13P3 + D-Glucose --> ADP C10H12N5O10P2 + D-Glucose 6-phosphate + H+

# #Yli has no Glucokinase in their models
# iYli20_model.summary()
# R1294 = iYli20_model.reactions.get_by_id('R1294') # D-glucose exchange M00032[e] <=>
# R1294

# M00032 = iYli20_model.metabolites.get_by_id('M00032[e]') # extracellular glucose
# M00032.summary() # consumed: 100% R1168 => M00032[c] D-glucose cytosol
# R1168 = iYli20_model.reactions.get_by_id('R1168') # D-glucose transport (uniport): M00032[e] --> M00032[c]
# R1168

# M00032 = iYli20_model.metabolites.get_by_id('M00032[c]') # cytosolic glucose
# for rxn in M00032.reactions: 
#     print(rxn.id, rxn.name, rxn.reaction, hf.formulaWithNames(rxn))

# iYli647_model.summary() # all good
# glc_D_e = iYli647_model.metabolites.get_by_id('glc_D[e]') # extracellular glucose
# glc_D_e.summary() # consumed: GLCt1 100% glucose transport uniport

# glc_D = iYli647_model.metabolites.get_by_id('glc_D[c]') # cytosolic glucose
# for rxn in glc_D.reactions:
#     print(rxn.id, rxn.name, rxn.reaction, hf.formulaWithNames(rxn)) # GLUK: glucokinase

r467 = iYali4_model.reactions.get_by_id('467') # glucose-6-phosphate isomerase: D-glucose 6-phosphate[cy] <=> D-fructose 6-phosphate[cy]: m296 <=> m166
r467
m166 = iYali4_model.metabolites.get_by_id('m166') # D-fructose 6-phosphate[cy]
m166.summary() # consumed: 100% 467

In [137]:
iMT1026v3_model.summary()

# check HEX1 and PGK
HEX = iMT1026v3_model.reactions.get_by_id('HEX1') # atp_c + glc_D_c --> adp_c + g6p_c + h_c
# HEX
# iMT1026v3_model.metabolites.get_by_id('glc_D_c').summary() # 40: GLUK; 60: HEX1
GLUK = iMT1026v3_model.reactions.get_by_id('GLUK') # atp_c + glc_D_c --> adp_c + g6p_B_c + h_c
GLUK 

g6p_c = iMT1026v3_model.metabolites.get_by_id('g6p_c') # glucose-6-phosphate
g6p_c.summary() # 40: GLUK; 60: HEX1; 100: PGK

# # PGI
# PGI = iMT1026v3_model.reactions.get_by_id('PGI') # g6p_c <=> f6p_c
# PGI # glucose-6-phosphate isomerase

f6p_c = iMT1026v3_model.metabolites.get_by_id('f6p_c') # fructose-6-phosphate
f6p_c.summary() # 89: PFK, 9: MAN6PI: man6p_c <=> f6p_c, 1.7: GF6PTA: f6p_c + gln_L_c --> gam6p_c + glu_L_c

# # # alternative to PGI
# G6PI3 = iMT1026v3_model.reactions.get_by_id('G6PI3') # g6p_B_c <=> f6p_c
# G6PI3 # Glucose-6-phosphate isomerase

# # PGK
# PGK = iMT1026v3_model.reactions.get_by_id('PGK') # 3pg_c + atp_c <=> 13dpg_c + adp_c
# PGK # phosphoglycerate kinase



#### iYli21: Compare reaction flux with FVA result
- FVA
- Read only reactions of interest

In [103]:
def test_fva(model, reactions, biomass_rxn, growth_condition, maintenance_rxn, maintenance, verbose=False):
    # set growth condition
    set_growth_condition(model, biomass_rxn, growth_condition, maintenance_rxn, maintenance)
    # compute FVA solution
    # pfba solution
    fva_solution = cobra.flux_analysis.flux_variability_analysis(model)
    if verbose:
        print(f'The objective value of the {model} is: {fva_solution.loc[biomass_rxn]}')
    # collect pathway intervals
    current_fva_interval = {}
    for ec_number, rxn_id in reactions.items():
        current_fva_interval[ec_number] = (fva_solution.loc[rxn_id].minimum, fva_solution.loc[rxn_id].maximum)
    return current_fva_interval

In [116]:
### create table with rxn_name; EC; model1_rxn_id; model2_rxn_id; model1_flux; model2_flux; 
# => compare fluxes of the same reaction in different models

# EXAMPLE:
# iYli21 results
model_name = 'iYli21'
print(f"{model_name}: \n")
biomass_rxn = 'biomass_C'
maintenance_rxn = 'xMAINTENANCE'
growth_condition = {
    'R1070': 100, # glucose
    'R1065': 0, # fructose
    'R1141': 0, # glycerol
}

fva_intervals = get_fva_intervals(iYli21_model, iYli21_citrate_cycle, biomass_rxn, growth_condition, maintenance_rxn, _yli_maintenance, verbose=False)
fva_intervals

iYli21: 



{'6.4.1.1': (46.766713339314734, 46.76671333970987),
 'pyruvate_mitochodrial_transport': (0.0, 53.098703907657125),
 '1.2.4.1': (49.77766800141687, 49.77766800144597),
 '2.3.3.1': (33.86215015014585, 33.8621501502076),
 '4.2.1.3': (-966.1378498498541, 1000.0),
 '1.1.1.41': (0.0, 1.7674750552032492e-10),
 '1.2.4.2': (15.532576024184657, 15.532576024231531),
 '2.3.1.61': (15.532576024184657, 15.532576024231531),
 '6.2.1.4': (15.532576024191911, 15.532576024241838),
 '1.3.5.1': (20.7111446789874, 20.711144679005194),
 '4.2.1.2': (15.532576024192934, 15.532576024272549),
 '1.1.1.37': (24.122473309395566, 1000.0)}

In [113]:
# fva_intervals.columns # Index(['minimum', 'maximum'], dtype='object')
for ec_number, rxn_id in iYli21_citrate_cycle.items():
    print(rxn_id, "min: ", fva_intervals.loc[rxn_id].minimum, "max: ", fva_intervals.loc[rxn_id].maximum)

R690 min:  46.76671333937453 max:  46.76671333971214
R1311 min:  0.0 max:  53.09870390767182
R693 min:  49.77766800116876 max:  49.777668001451204
R236 min:  33.86215015014558 max:  33.862150150178906
R238 min:  -966.1378498498544 max:  1000.0
R487 min:  0.0 max:  1.3599787962448318e-11
R614 min:  15.532576024184664 max:  15.53257602423472
R613 min:  15.532576024184664 max:  15.53257602423472
R741 min:  15.53257602423696 max:  15.5325760242442
R740 min:  20.711144679031896 max:  20.711144679075705
R314 min:  15.53257602422184 max:  15.532576024249906
R533 min:  24.122473309421416 max:  1000.0


#### Postprocessing of FVA + Flux table (round the table, range over all model fva results)
- load the data table
- round the data on 5 digits

In [264]:
# load the data table

fva_flux_table = pd.read_csv(f"{config['results']['metabolic_fluxes']}/{_condition}_flux_fva.csv", sep=config['seperator'], index_col=False)
fva_flux_table.head()
# round all numerical values to 3
fva_flux_table = fva_flux_table.round(3)
_round_condition = "rounded_" + _condition
fva_flux_table.to_csv(f"{config['results']['metabolic_fluxes']}/{_round_condition}_flux_fva.csv", sep=config['seperator'], index=False)

#### Get E. coli and change IDs to use connection information for each model
- get ecoli escher model
- find the connecting ids and how to modify them
- write algorithm to find and match the enzyme names between e coli and iYli21 (generic)
- change the IDs of the escher map and map the core metabolism to iYli21 in escher


In [275]:
# tutorial of escher
import escher
from escher import Builder

# set map name and model name -> connection
builder = Builder(
    map_name='iMM904.Central carbon metabolism',
    model_name='iMM904',
)
# load ecoli model
builder.model = cobra.io.read_sbml_model(config['models']['scere']) # ecoli core
# Run FBA with the model and add the flux data to the map
solution = builder.model.optimize()
builder.reaction_data = solution.fluxes


In [276]:
builder

Builder(reaction_data={'CITtcp': 0.0, '13BGH': 0.0, '13BGHe': 0.0, '13GS': 0.32667000056331835, '16GS': 0.0, '…

In [305]:
## load json map for mapping with reaction_names of the models of interest
import json
import pathway2cyjs as p2c
reload(p2c)

with open(config['escher']['scere'], "r") as read_file:
    # scere_map = json.load(read_file)
    cyelements = p2c.escher2cyelements(read_file)
    p2c.cyelements2cyjs(cyelements, 'scere_map')  
# scere_map
# len(scere_map)
# scere_map[0] # meta data
# scere_map[1].keys() # dict_keys(dict_keys(['reactions', 'nodes', 'text_labels', 'canvas'])
# reactions = scere_map[1]['reactions'] # length: 72

# for rxn in reactions.items():
#     # print(rxn)


save cyelements as scere_map


#### Match S. cerevisiae und iYli21 + iMT1026v3
- Load models
- Find best fitting rxn id (BIGG ID)
    - Test with glycolysis, ppp, citric acid cycle
    - Iterate over rxn names and match them to rxn names from S cere model
    - if match: store corresponding rxn in dict
    - {model: {'BIGG_id_x': 'rxn_id'}}
    - Count the number of rxns found
    - Change only the IDs to the bigg ids (maybe also the rxn names)
- old_id = BIGG ID (=> matching der Daten mit KEGG möglich (über BiKEGG))

In [8]:
# load S. cerevisiae model
scere_model = cobra.io.read_sbml_model(config['models']['scere'])

# load iYli21 model
iYli21_model = cobra.io.read_sbml_model(config['models']['yli21'])

# load iMT1026v3 model
iMT1026v3_model = cobra.io.read_sbml_model(config['models']['ppa1026v3'])

Model does not contain SBML fbc package information.
SBML package 'layout' not supported by cobrapy, information is not parsed
SBML package 'render' not supported by cobrapy, information is not parsed
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_oligoP_v "oligophosphate (5-P)">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_polyP_v "polyphosphate (100-P)">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_h2o_v "H2O">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_h2o_c "H2O">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_ppi_c "Diphosphate">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_h_c "H+">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_pi_c

##### Prepare iMT1026 (find rxns from glycolysis, citric acid cycle and ppp)

In [79]:
# get all rxn_ids from iMT1026v3 for the pathways of interest 
pathways_of_interest = ['glycolysis', 'citric acid cycle', 'pentose phosphate pathway']
reactions_of_interest = {}

# reactions_of_interest: {
    # 'glycolysis': {
    #     'iYli21': set(),
    #     'iMT1026v3': set(),
    #     'scere': set(),
    # },
    # 'citrate_cycle': {
    #     'iYli21': set(),
    #     'iMT1026v3': set(),
    #     'scere': set(),
    # },
    # 'pentose_phosphate_pathway': {
    #     'iYli21': set(),
    #     'iMT1026v3': set(),
    #     'scere': set(),
    # },
# }
# get only glycolysis reactions from iMT1026v3 (found 2 Pentose phosphate pathway groups (11, 5 Reactions))
def get_rxn_id_from_group(group):
    rxn_id = []
    for rxn in group.members:
        rxn_id.append(rxn.id)
    return rxn_id

for group in iMT1026v3_model.groups:
    for pathway in pathways_of_interest:
        if pathway in group.name.lower():
            # if pathway exists in dict: add another group
            if pathway in reactions_of_interest.keys():
                # add list of reaction ids to existing list of reactions
                reactions_of_interest[pathway]['iMT1026v3'].append(get_rxn_id_from_group(group))
                continue
            # else: create new dict entry with reaction ids
            reactions_of_interest[pathway] = {}
            reactions_of_interest[pathway]['iMT1026v3'] = [get_rxn_id_from_group(group)]

matched_reactions = {}
for pathway, model_rxns in reactions_of_interest.items():
    print(f'Comparing {pathway} ({len(model_rxns.values())} reactions):')
    for model, rxns in model_rxns.items():
        print(f'    {model}:')
        for rxn_list in rxns: # rxns = [[rxn1, rxn2], [rxn3, rxn4]]
            # match rxn ids with Scere model
            for rxn_model in rxn_list:
                for rxn_truth in scere_model.reactions:
                    if rxn_model == rxn_truth.id:
                        matched_reactions[rxn_truth.id] = rxn_model
                        break
matched_reactions    

Comparing citric acid cycle (1 reactions):
    iMT1026v3:
Comparing glycolysis (1 reactions):
    iMT1026v3:
Comparing pentose phosphate pathway (1 reactions):
    iMT1026v3:


{'AKGDbm': 'AKGDbm',
 'ICDHyp': 'ICDHyp',
 'SUCD2_u6m': 'SUCD2_u6m',
 'ICDHxm': 'ICDHxm',
 'AKGDam': 'AKGDam',
 'SUCOASm': 'SUCOASm',
 'MDHm': 'MDHm',
 'ACONTm': 'ACONTm',
 'ITCOALm': 'ITCOALm',
 'FUM': 'FUM',
 'ICDHym': 'ICDHym',
 'ACONT': 'ACONT',
 'CSp': 'CSp',
 'FUMm': 'FUMm',
 'MDH': 'MDH',
 'CSm': 'CSm',
 'FBA2': 'FBA2',
 'PFK_2': 'PFK_2',
 'FBA3': 'FBA3',
 'PYK': 'PYK',
 'G6PI3': 'G6PI3',
 'HEX7': 'HEX7',
 'PGM': 'PGM',
 'PFK_3': 'PFK_3',
 'FBA': 'FBA',
 'TPI': 'TPI',
 'G6PI': 'G6PI',
 'GLUK': 'GLUK',
 'PGK': 'PGK',
 'DPGM': 'DPGM',
 'GAPD': 'GAPD',
 'ENO': 'ENO',
 'HEX4': 'HEX4',
 'PFK': 'PFK',
 'HEX1': 'HEX1',
 'FBP': 'FBP',
 'PGI': 'PGI',
 'PGL': 'PGL',
 'RBK': 'RBK',
 'TKT2': 'TKT2',
 'GND': 'GND',
 'TKT1': 'TKT1',
 'PPM': 'PPM',
 'RPE': 'RPE',
 'DRBK': 'DRBK',
 'RPI': 'RPI',
 'TALA': 'TALA',
 'PRPPS': 'PRPPS'}

In [80]:
iMT_glycolysis = reactions_of_interest['glycolysis']['iMT1026v3'][0]
iMT_glycolysis

iMT_citric = reactions_of_interest['citric acid cycle']['iMT1026v3'][0]
iMT_citric

['ICDOXSUCm',
 'AKGDbm',
 'ICDHyp',
 'OSUCCCLm',
 'SUCD2_u6m',
 'ACONTx',
 'ICDHxm',
 'AKGDam',
 'SUCOASm',
 'MDHm',
 'ICDOXSUC',
 'ACONTm',
 'ITCOALm',
 'AKGDH2',
 'OSUCCCL',
 'FUM',
 'ICDHym',
 'AKGDH1',
 'ACONT',
 'CSp',
 'ICDHy',
 'FUMm',
 'MDH',
 'CSm']

In [4]:
# match reaction names with levenshtein distance (edit distance)
import math
import Levenshtein as lev

def match_rxn_names(rxns_of_interest, verified_rxns, model_name, bigg_ids=None, verbose=False):
    """Iterate over rxns_of_interest and match reaction names with verified_rxns.
    Returns dict of matched reactions with model_name as key and rxn_id as value.
    Adds bigg_ids to bigg_ids dict if provided. Missing matches are set to '-'.
    @param rxns_of_interest: list of reaction ids
    @param verified_rxns: dict of verified reactions (['name']['bigg_id']) (see BIGG Models API response)
    @return: dict keys: model_rxn_id, values: bigg_id
    """
    if bigg_ids == None:
        bigg_ids = {}
    bigg_ids[model_name] = {}
    matched_rxns = {}
    for rxn_id in rxns_of_interest:
        lev_dist = math.inf
        best_match = '-'
        rxn_name = iMT1026v3_model.reactions.get_by_id(rxn_id).name.lower()

        for rxn in verified_rxns:
            if rxn['name'] == None:
                continue
            curr_lev_dist = lev.distance(rxn_name, rxn['name'].lower())
            if curr_lev_dist < lev_dist:
                lev_dist = curr_lev_dist
                best_match = rxn['bigg_id']
        # set bigg id for model
        matched_rxns[rxn_id] = best_match
        bigg_ids[model_name] = matched_rxns # because multiple reactions might be not found
        if verbose:
            model_rxn = iMT1026v3_model.reactions.get_by_id(rxn_id)
            verified_rxn_name = [rxn['name'] for rxn in verified_rxns if rxn['bigg_id'] == best_match][0]
            print(f'----\nmodel: {model_rxn.name} ({rxn_id})\nbigg: {verified_rxn_name} ({best_match})\nlev dist: {lev_dist}\n----\n')
    return bigg_ids

#### Playing with BIGG API for reaction names

In [5]:
# request BIGG API for reaction names
import requests

bigg_rxns = requests.get('http://bigg.ucsd.edu/api/v2/universal/reactions')
bigg_rxns.json()
# len(bigg_rxns.json()['results']) # 1577 reactions (matches with the number of reactions in the model)

# find bigg ids for the reactions of interest
bigg_ids = {}
## All reactions:
all_reactions = [rxn.id for rxn in iMT1026v3_model.reactions]
# iterate model reactions
bigg_ids = match_rxn_names(all_reactions, bigg_rxns.json()['results'], 'iMT1026v3', None, verbose=True)

###### Add this for all reactions and all models


## Citric acid cycle



# iMT1026v3:
# Glycolysis
# 24 reactions to be found (one odd)     
# Problem: model: pyruvate dehydrogenase dihydrolipoamide dehydrogenase
# bigg: Oxoglutarate dehydrogenase  dihydrolipoamide S succinyltransferase 
# lev dist: 25---- (correct: PDHcr) (Pyruvate dehydrogenase (dihydrolipoamide) reversible)

# Citric acid cycle


# iYli21:


NameError: name 'iMT1026v3_model' is not defined

In [90]:
## kegg, get only reactions you are interested in
# yli_M00009 (TCA)
import KEGGutils as kg
pathway = kg.KEGGpathway(pathway_id = "hsa05215")
print(pathway.title)


Prostate cancer


In [107]:
# print(kg.KEGGpathway.__doc__)
# glycolysis: yli00010
# citrate cycle: yli00020
pathway = kg.KEGGpathway(pathway_id = "yli00010")

# get all reactions of pathway
pathway.title # carbon metabolism
pathway.reactions # 55 reactions
# was sind das für names und ids? -> keine bigg ids


{'46': {'id': '46',
  'name': 'rn:R01518',
  'type': 'reversible',
  'substrates': [(146, 'cpd:C00631')],
  'products': [(63, 'cpd:C00197')]},
 '47': {'id': '47',
  'name': 'rn:R01512',
  'type': 'reversible',
  'substrates': [(63, 'cpd:C00197')],
  'products': [(143, 'cpd:C00236')]},
 '48': {'id': '48',
  'name': 'rn:R00755',
  'type': 'irreversible',
  'substrates': [(103, 'cpd:C05125')],
  'products': [(105, 'cpd:C00084')]},
 '52': {'id': '52',
  'name': 'rn:R00014',
  'type': 'irreversible',
  'substrates': [(146, 'cpd:C00068'), (102, 'cpd:C00022')],
  'products': [(103, 'cpd:C05125')]},
 '54': {'id': '54',
  'name': 'rn:R02569',
  'type': 'reversible',
  'substrates': [(107, 'cpd:C15973'), (104, 'cpd:C00024')],
  'products': [(106, 'cpd:C16255')]},
 '57': {'id': '57',
  'name': 'rn:R00200',
  'type': 'irreversible',
  'substrates': [(96, 'cpd:C00074')],
  'products': [(102, 'cpd:C00022')]},
 '59': {'id': '59',
  'name': 'rn:R00658',
  'type': 'reversible',
  'substrates': [(89, 'c

In [83]:
# change models ids to bigg ids
len(bigg_ids['iMT1026v3']) # 48 len

# iterate bigg_ids
for model, rxns in bigg_ids.items():
    for rxn_id, bigg_id in rxns.items():
        # find rxn in model
        rxn = iMT1026v3_model.reactions.get_by_id(rxn_id)
        # change id to bigg id
        rxn.id = bigg_id
        # save model

# save model
output_name = config['models']['iMT1026v3'].split('.')[0] + '_bigg.xml'
cobra.io.write_sbml_model(iMT1026v3_model, output_name)


ValueError: The model already contains a reaction with the id: PFK

In [8]:
from Levenshtein import distance
pathways_of_interest = ['glycolysis', 'citric acid cycle', 'pentose phosphate pathway']
reactions_of_interest = {}


#### Max ideen:

In [2]:
import requests
import re

response = requests.post(
    'http://bigg.ucsd.edu/advanced_search_external_id_results',
    data={'database_source': 'kegg.compound', 'query': 'C00234'}
)

try:
    print(re.search(r'/models/universal/metabolites/([^"]+)', response.text).group(1))
except AttributeError:
    print('no result')

10fthf


In [3]:
for x in response:
    print(x)

b'<!DOCTYPE html>\n<html lang="en">\n  <head>\n    <title>BiGG Models</title>\n\n    <!-- Bootstrap and jQuery -->\n    <script src="//c'
b'ode.jquery.com/jquery-1.9.1.min.js"></script>\n    <script src="//netdna.bootstrapcdn.com/bootstrap/3.3.6/js/bootstrap.min.js"></'
b'script>\n    <link rel="stylesheet" href="//netdna.bootstrapcdn.com/bootstrap/3.3.6/css/bootstrap.min.css"/>\n    <link rel="style'
b'sheet" href="//netdna.bootstrapcdn.com/font-awesome/4.0.3/css/font-awesome.min.css"/>\n\n    <!-- BiGG styles and js -->\n    <scri'
b'pt src="/static/js/script.js"></script>\n    <script src="/static/js/question_mark.js"></script>\n    <link rel="stylesheet" href='
b'"/static/css/style.css"/>\n\n    <!-- Favicon -->\n    <link rel="icon" type="image/png" href="/static/assets/favicon.ico">\n\n    <m'
b'eta charset="utf-8"/>\n    <meta name="viewport" content="width=device-width, initial-scale=1.0, maximum-scale=1.0, user-scalable'
b'=no"/>\n    <meta name="google" content="notranslate">

#### Metabolic maps only possible with BiKEGG in MATLAB
- Search for the reactions (id and name)
- Compare the found reactions between iYli21 and iMT1026v3 (based on name)
- Compare the found reactions with the reaction list

In [3]:
# imports 
import cobra
import sys 

sys.path.append('../scripts/')
import helperFunction as hf

config = hf.load_config()

In [7]:
# load models and find groups:
# models dictionary
models = {
        'iYli21': config['models']['yli21'],
        'iMT1026v3': config['models']['ppa1026v3'],
        'iLC915': config['models']['ppaiLC915'],
        'iYali4_corr': config['models']['yli4_corr'], 
        'iYali4_uncorr': config['models']['yli4_uncorr'], 
        'yli647_corr': config['models']['yli647_corr'], 
        'yli647_uncorr': config['models']['yli647_uncorr'], 
        'iYli_2.0_corr': config['models']['yli2.0_corr'], 
        'iMK735_corr': config['models']['yliMK735_corr'], 
        'iMK735_uncorr': config['models']['yliMK735_uncorr'], 
        'iNL895_corr': config['models']['yliNL895_corr'],
        'iNL895_uncorr': config['models']['yliNL895_uncorr'],
        'PpaMBEL1254': config['models']['ppaMBEL1254'],
        'iMT1026Chan2017': config['models']['ppa1026Chan'],
    }


In [8]:
counter = 0
# load iYli21 get names of citrate cycle 
for model_name, model_path in models.items():
    print(model_name)
    # load model
    model = cobra.io.read_sbml_model(model_path)
    print(model.groups)
    if counter > 2:
        break
    counter += 1
# => iYli21, iYali4, iMT1026v3 haben diese groups

iYli21
[<Group group1 at 0x2ac22cc70>, <Group group2 at 0x2ac22cd30>, <Group group3 at 0x2ac008670>, <Group group4 at 0x2ac01f6d0>, <Group group5 at 0x2ac01f670>, <Group group6 at 0x2ac22c940>, <Group group7 at 0x2ac22ca90>, <Group group8 at 0x2ac22ce80>, <Group group9 at 0x2ac22cdf0>, <Group group10 at 0x2ac22ce50>, <Group group11 at 0x2a495d4c0>, <Group group12 at 0x2ac2efc40>, <Group group13 at 0x2ac2efd00>, <Group group14 at 0x2ac2efd30>, <Group group15 at 0x2ac2efd90>, <Group group16 at 0x2ac2efc10>, <Group group17 at 0x2ac2efe20>, <Group group18 at 0x2ac2efe50>, <Group group19 at 0x2ac2efcd0>, <Group group20 at 0x2ac2efe80>, <Group group21 at 0x2ac2efdf0>, <Group group22 at 0x2ac2eff10>, <Group group23 at 0x2ac2efee0>, <Group group24 at 0x2ac2efeb0>, <Group group25 at 0x2ac2eff70>, <Group group26 at 0x2ac2eff40>, <Group group27 at 0x2ac2effd0>, <Group group28 at 0x2ac2efc70>, <Group group29 at 0x2ac2effa0>, <Group group30 at 0x2ac2efca0>, <Group group31 at 0x2ac2efdc0>, <Group gr

Model does not contain SBML fbc package information.
SBML package 'layout' not supported by cobrapy, information is not parsed
SBML package 'render' not supported by cobrapy, information is not parsed
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_oligoP_v "oligophosphate (5-P)">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_polyP_v "polyphosphate (100-P)">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_h2o_v "H2O">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_h2o_c "H2O">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_ppi_c "Diphosphate">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_h_c "H+">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_pi_c

[<Group Transport, Nuclear at 0x32c52f250>, <Group Fatty Acid Biosynthesis at 0x2ac291e80>, <Group Transport, ER at 0x32c4c6f70>, <Group Phospholipid Metabolism at 0x32c600970>, <Group Transport, Golgi Apparatus at 0x32c600a00>, <Group Sphingolipid metabolism at 0x32c600850>, <Group Oxidative Phosphorylation at 0x32c600be0>, <Group Nucleotide Metabolism at 0x32c600520>, <Group Sphingolipid Metabolism at 0x32c600b50>, <Group Polyphosphate metabolism at 0x32c600430>, <Group Tyrosine, Tryptophan, and Phenylalanine Metabolism at 0x32c6007c0>, <Group Pyridoxine Metabolism at 0x32c600c70>, <Group Glycine and Serine Metabolism at 0x32c6009a0>, <Group Glycosylation pathway at 0x32c600c10>, <Group Other at 0x32c600940>, <Group Biomass Composition at 0x32c600460>, <Group Carbohydrate metabolism at 0x32c600730>, <Group Fatty Acid Degradation at 0x32c600f10>, <Group Transport, Mitochondrial at 0x32c600490>, <Group Sterol Metabolism at 0x32c6005b0>, <Group Inositol phosphate metabolism at 0x32c6006

In [14]:
# fix iMT1026v3: because errors are anoying
import os

def read_and_write_model(input_path, outdir=None):
    split_path = input_path.split('/')
    file_name = split_path[-1].split('.')[0]
    model = cobra.io.read_sbml_model(input_path)
    outpath = os.path.join('/'.join(split_path[:-1]), file_name + '_read_write.xml') if not outdir else outdir + file_name + '_read_write.xml'
    cobra.io.write_sbml_model(model,outpath)
    return outpath

read_and_write_model(config['models']['ppa1026v3'], '/Users/ampholyt/Coding/BSEP22/Code/With_Bockmayr/carbon-souces-yli/data/models/read_write_cobrapy/')


Model does not contain SBML fbc package information.
SBML package 'layout' not supported by cobrapy, information is not parsed
SBML package 'render' not supported by cobrapy, information is not parsed
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_oligoP_v "oligophosphate (5-P)">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_polyP_v "polyphosphate (100-P)">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_h2o_v "H2O">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_h2o_c "H2O">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_ppi_c "Diphosphate">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_h_c "H+">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_pi_c

'/Users/ampholyt/Coding/BSEP22/Code/With_Bockmayr/carbon-souces-yli/data/models/read_write_cobrapy/Ppa_iMT1026v3_v2_read_write.xml'

#### check groups from iYli21, iYali4
- load models
- find citrate cycle group
- compare the group members for each model
- find citric acid cycle group
- compare the group members (table)


In [10]:

iYli21_model = cobra.io.read_sbml_model(config['models']['yli21'])
iYali4_corr_model = cobra.io.read_sbml_model(config['models']['yli4_corr'])
iYali4_uco_model = cobra.io.read_sbml_model(config['models']['yli4_uncorr'])
iYli20_model = cobra.io.read_sbml_model(config['models']['yli2.0_corr'])
# 42 sec

Model does not contain SBML fbc package information.
SBML package 'layout' not supported by cobrapy, information is not parsed
SBML package 'render' not supported by cobrapy, information is not parsed
Encoding LOWER_BOUND and UPPER_BOUND in KineticLaw is discouraged, use fbc:fluxBounds instead: <Reaction R_1 "(R)-lactate:ferricytochrome-c 2-oxidoreductase">
Use of GENE ASSOCIATION or GENE_ASSOCIATION in the notes element is discouraged, use fbc:gpr instead: <Reaction R_1 "(R)-lactate:ferricytochrome-c 2-oxidoreductase">
Encoding LOWER_BOUND and UPPER_BOUND in KineticLaw is discouraged, use fbc:fluxBounds instead: <Reaction R_2 "(R)-lactate:ferricytochrome-c 2-oxidoreductase">
Use of GENE ASSOCIATION or GENE_ASSOCIATION in the notes element is discouraged, use fbc:gpr instead: <Reaction R_2 "(R)-lactate:ferricytochrome-c 2-oxidoreductase">
Encoding LOWER_BOUND and UPPER_BOUND in KineticLaw is discouraged, use fbc:fluxBounds instead: <Reaction R_4 "(S)-lactate:ferricytochrome-c 2-oxidore

In [4]:
# find glycolisis
# for group in iYli21_model.groups:
#     # if 'carbon metabolism' in group.name.lower(): # Carbon metabolism 1
#     #     print(group.id, group.name, len(group.members))
#     if 'glycolysis' in group.name.lower(): # Glycolysis 27 (group36)
#         print(group.id, group.name, len(group.members)) 
#     if 'citrate' in group.name.lower(): # TCA 17 (group14)
#         print(group.id, group.name, len(group.members))
#     if 'pentose phosphate' in group.name.lower(): # PPP: 13 (group55)
#         print(group.id, group.name, len(group.members))

# # analysis carbon metabolism (unimportant)
# for member in iYli21_model.groups.get_by_id('group13').members:
#     print(member.id, member.name)
#     # => R720 sedoheptulose 1,7-bisphosphate D-glyceraldehyde-3-phosphate-lyase

# # analysis glycolisis
# yli21_interesting_groups = ['group36', 'group14', 'group55']
# #                        glycolysis, citrate cycle, pentose phosphate pathway
# glycolisis_rxn_id = []
# glycolisis_rxn_name = []
# for member in iYli21_model.groups.get_by_id('group36').members:
#     glycolisis_rxn_id.append(member.id)
#     glycolisis_rxn_name.append(member.name)

# # dataframe
# import pandas as pd
# glycolisis_df_iYli21 = pd.DataFrame({'rxn id': glycolisis_rxn_id, 'rxn name': glycolisis_rxn_name})
# glycolisis_df_iYli21
# load Sce and check for reactions
Sce_model = cobra.io.read_sbml_model(config['models']['scere'])
Sce_model



<Model iMM904 at 0x137afcb50>

In [55]:
# escher map load and investigate the reactions 
import escher
from escher import Builder
from time import sleep


ecoli_model = cobra.io.read_sbml_model(config['models']['ecoli'])

builder = Builder(
    height=600,
    map_name=None,
    model_name='e_coli_core',
    map_json='https://escher.github.io/1-0-0/5/maps/Escherichia%20coli/e_coli_core.Core%20metabolism.json',
)
reverse = False
step = 0.1
timestep = 0.1
duration = 15 # seconds
lim = [0, 0.5]
val = lim[-1]
for _ in range(int(duration / timestep)):
    print(val, -val)
    ecoli_model.reactions.EX_o2_e.lower_bound = -val
    solution = ecoli_model.optimize()
    builder.reaction_data = solution.fluxes
    if val <= lim[0]:
        reverse = True
    if val >= lim[1]:
        reverse = False
    if reverse:
        val += step
    else:
        val -= step
    sleep(timestep)

0.5 -0.5
0.4 -0.4
0.30000000000000004 -0.30000000000000004
0.20000000000000004 -0.20000000000000004
0.10000000000000003 -0.10000000000000003
2.7755575615628914e-17 -2.7755575615628914e-17
-0.09999999999999998 0.09999999999999998


/Users/ampholyt/Coding/BSEP22/Code/With_Bockmayr/EFM_calculation_cobamp/venv/lib/python3.8/site-packages/cobra/util/solver.py:554: UserWarning: Solver status is 'infeasible'.
  warn(f"Solver status is '{status}'.", UserWarning)


2.7755575615628914e-17 -2.7755575615628914e-17
0.10000000000000003 -0.10000000000000003
0.20000000000000004 -0.20000000000000004
0.30000000000000004 -0.30000000000000004
0.4 -0.4
0.5 -0.5
0.4 -0.4
0.30000000000000004 -0.30000000000000004
0.20000000000000004 -0.20000000000000004
0.10000000000000003 -0.10000000000000003
2.7755575615628914e-17 -2.7755575615628914e-17
-0.09999999999999998 0.09999999999999998
2.7755575615628914e-17 -2.7755575615628914e-17
0.10000000000000003 -0.10000000000000003
0.20000000000000004 -0.20000000000000004
0.30000000000000004 -0.30000000000000004
0.4 -0.4
0.5 -0.5
0.4 -0.4
0.30000000000000004 -0.30000000000000004
0.20000000000000004 -0.20000000000000004
0.10000000000000003 -0.10000000000000003
2.7755575615628914e-17 -2.7755575615628914e-17
-0.09999999999999998 0.09999999999999998
2.7755575615628914e-17 -2.7755575615628914e-17
0.10000000000000003 -0.10000000000000003
0.20000000000000004 -0.20000000000000004
0.30000000000000004 -0.30000000000000004
0.4 -0.4
0.5 -

In [56]:
builder = Builder(
    map_name='e_coli_core.Core metabolism',
    model_name='e_coli_core',
)

In [57]:
builder

Builder()

-0.4

In [37]:
builder

In [ ]:
# Check from iMT1026v3

# Check table

#### Set up metabolic map for S. cerervisiae


In [2]:
# load Sce
sce_model = cobra.io.read_sbml_model(config['models']['scere'])
sce_model


<Model iMM904 at 0x10b0db8e0>

In [8]:
sce_model.summary()

In [3]:
sol = sce_model.optimize()


In [4]:
# escher
import escher
from escher import Builder
# print(escher.list_available_maps())

# print(escher.list_available_models())



### Notes about meeting with Tom, Bockmayr and Frederik:
km: how well does the substrate bind (in mmol range the binding is good) (nanomolar)
kcat: how fast does the enzyme work
preKcat - jkslab

- It depends on your condition (just interested in biomass)

- FBA Lösung 
- (optimale solution nicht zu sehr verändern beim null setzen)
- 

- EFMs:
- differenzen der irreversiblen reaktionen zwischen EFM und optimalen solution minimieren

- Wie könnte man feststellen, ob es numerische probleme sind? 
    - Dann könnte man die Werte nach dem gap mal exemplatorisch

In [5]:
# builder
builder = Builder(
    map_name='iMM904.Central carbon metabolism',
    model_name='iMM904',
)

# add FBA results
builder.reaction_data = sol.fluxes
# Add some data for metabolites
builder.metabolite_data = sol.shadow_prices

In [14]:
builder

Builder(metabolite_data={'2dr5p_c': -0.0, '2hb_c': -0.037418581843231914, '2hb_e': -0.037418581843231914, '2hh…